In [1]:
from ekv_functions import *

import numpy as np
from numpy import pi as pi
from numpy import log as ln
from numpy import log10 as log
from numpy import sqrt as sqrt
from numpy import exp as exp
from numpy import arctan as atan
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.ticker import EngFormatter
plt.style.use('plt_style.mplstyle')
import subprocess
import shutil
import os
import os.path as op
import sys
import re

from matplotlib.ticker import EngFormatter
from IPython.display import display, Latex

sys.path.append(".")

#plt.rcParams['text.usetex'] = True
plt.rcParams['svg.fonttype'] = 'none'
plt.rcParams['pdf.fonttype'] = 42
#plt.rcParams['ps.fonttype'] = 42
plt.rcParams['font.family'] = 'Arial'
#plt.rcParams['mathtext.fontset'] = 'cm'

plt.rcParams['mathtext.fontset'] = 'custom'
plt.rcParams['mathtext.rm'] = 'Arial'
plt.rcParams['mathtext.it'] = 'Arial:italic'
plt.rcParams['mathtext.bf'] = 'Arial:bold'

plt.style.use('plt_style_small.mplstyle')
lw=1
msize=4
mevery=4

refloat=r'.*?([+-]?\d+([.]\d*)?([eE][+-]?\d+)?|[.]\d+([eE][+-]?\d+)?)'

kB=1.38064852E-23
q=1.60217662E-19
T0=273.15
epsilon0=8.854E-12
epsilonox=3.9
TC=27
T=T0+TC
kT=kB*T
UT=kT/q

type='nmos'
Type='nMOS (t-t)'

#newSim=True
newSim=False

def diff(y, dx):
    N=len(y)
    dydx=np.zeros(N)
    dydx[0]=(y[1]-y[0])/dx
    dydx[1]=(y[2]-y[0])/(2*dx)
    for k in range(2,N-2):
        dydx[k]=(y[k-2]-8*y[k-1]+8*y[k+1]-y[k+2])/(12*dx)
    dydx[N-2]=(y[N-1]-y[N-3])/(2*dx)
    dydx[N-1]=(y[N-1]-y[N-2])/dx
    return dydx

# Introduction

In this notebook we will extract the sEKV parameters for nMOS transistors of the 130nm bulk CMOS process from IHP. The extraction is done with data generated by PSP for the typical-typical (t-t) case.

# Transistor geometry parameters

## Effective length and width for current

Before we start the extraction we need to account for the geometry dependence. With PSP you can choose between geometry scaling rules or binning rules with parameter $SWGEO$. If $SWGEO=1$, the scaling rules are chosen. This is the case in the IHP 130nm G2 PDK. The geometrical parameters are defined in @fig-cross_section.

![Definition of transistor geometrical parameters.](Figures/transistor_cross_section.png){#fig-cross_section}

The effective length and width are defined as

\begin{align}
  L_{eff} &= L - \Delta L,\\
  W_{eff} &= W_f - \Delta W,
\end{align}

where $W_f$ is the width of one finger defined as

\begin{equation}
  W_f = \frac{W}{NF}.
\end{equation}

In our case we will assume that the number of fingers $NF=1$ and hence that $W_f = W$.

$\Delta L$ and $\Delta W$ are given by

\begin{align}
  \Delta L &= 2\,LAP - \Delta L_{PS},\\
  \Delta W &= 2\,WOT - \Delta W_{OD},
\end{align}

with

\begin{align}
  \Delta L_{PS} &= LVARO \cdot \left(1+LVARL \cdot \frac{L_{EN}}{L}\right) \cdot \left(1+LVARW \cdot \frac{W_{EN}}{W_f}\right),\\
  \Delta W_{OD} &= WVARO \cdot \left(1+WVARL \cdot \frac{L_{EN}}{L}\right) \cdot \left(1+WVARW \cdot \frac{W_{EN}}{W_f}\right).
\end{align}

In the IHP 130nm G2 DPK $LVARO=0$ and $WVARO=0$ for nMOS (not for pMOS!). Therefore $\Delta L_{PS}=0$ and $\Delta W=0$ and $\Delta L$ and $\Delta W$ are simply given by

\begin{align}
  \Delta L &= 2\,LAP,\\
  \Delta W &= 2\,WOT.
\end{align}

They are given below.

In [2]:
def effectiveL(W,L):
    DLPS=lvaro*(1+lvarl*LEN/L)*(1+lvarw*WEN/W)
    return L+DLPS-2*lap

def effectiveW(Wf,L):
    DWOD=wvaro*(1+wvarl*LEN/L)*(1+wvarw*WEN/Wf)
    return Wf+DWOD-2*wot

LEN=1e-6
WEN=1e-6

# Parameters to calculate the effective length and width for pMOS extracted from sg13g2_moslv_parm.lib
lvaro = 0.0
lvarl = 0.0
lvarw = 0.0
lap = 2.9423e-08
wvaro = 0.0
wvarl = 0.0
wvarw = 0.0
wot = -1e-08

W=1e-6
L=1e-6
Leff=effectiveL(W,L)
Weff=effectiveW(W,L)

display(Latex(f'$L =$ {L/1e-6:.3f} $\\mu m$'))
display(Latex(f'$L_{{eff}} =$ {Leff/1e-6:.3f} $\\mu m$'))
display(Latex(f'$W =$ {W/1e-6:.3f} $\\mu m$'))
display(Latex(f'$W_{{eff}} =$ {Weff/1e-6:.3f} $\\mu m$'))

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

In [3]:
# Extracted from sg13g2_moslv_parm.lib
# Since lvaro=0 and wvaro=0 we can set DeltaLPS=0 and DeltaLWOD=0. DWn and DLn are then simply given by
DLn=2*lap
DWn=2*wot

display(Latex(f'$DL =$ {DLn/1e-9:.0f} nm'))
display(Latex(f'$DW =$ {DWn/1e-9:.0f} nm'))

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Note that $DWn$ is negative (width gets larger).

## Effective length and width for capacitances

The effective length and width are slightly different for the calulation of the capacitances.

The effective length and width for the calculation of the intrinsic and overlap acacitances are defined as

\begin{align}
  L_{E,CV} &= L - \Delta L_{CV},\\
  W_{E,CV} &= W - \Delta W_{CV},
\end{align}

where

\begin{align}
  \Delta L_{CV} &= 2\,LAP - \Delta L_{PS} - DLQ,\\
  \Delta W_{CV} &= 2\,WOT - \Delta W_{OD} - DWQ.
\end{align}

As mentioned above, for the IHP 130nm for nMOS $\Delta L_{PS}=0$ and $\Delta W_{OD}=0$ so that

\begin{align}
  \Delta L_{CV} &= 2\,LAP - DLQ,\\
  \Delta W_{CV} &= 2\,WOT- DWQ.
\end{align}

The effective length and width for the calculation of the fringing field capacitances are defined as

\begin{align}
  L_{G,CV} &= L - \Delta L_{G,CV},\\
  W_{G,ov} &= W - \Delta W_{G,CV},
\end{align}

where

\begin{align}
  \Delta L_{G,CV} &= - \Delta L_{PS} - DLQ,\\
  \Delta W_{G,CV} &= - \Delta W_{OD} - DWQ.
\end{align}



In [4]:
def effectiveLCV(Wf,L):
    DLPS=lvaro*(1+lvarl*LEN/L)*(1+lvarw*WEN/Wf)
    return L+DLPS-2*lap+dlq

def effectiveWCV(Wf,L):
    DWOD=wvaro*(1+wvarl*LEN/L)*(1+wvarw*WEN/Wf)
    return Wf+DWOD-2*wot+dwq

def effectiveLCVG(Wf,L):
    DLPS=lvaro*(1+lvarl*LEN/L)*(1+lvarw*WEN/Wf)
    return L+DLPS+dlq

def effectiveWCVG(Wf,L):
    DWOD=wvaro*(1+wvarl*LEN/L)*(1+wvarw*WEN/Wf)
    return Wf+DWOD+dwq

# Extracted from sg13g2_moslv_parm.lib
pre_layout = 1
dlq = -1.3721e-08-(1-pre_layout)*2e-08
dwq = -1e-08 

Lcv=effectiveLCV(W,L)
Wcv=effectiveWCV(W,L)
Lcvg=effectiveLCVG(W,L)
Wcvg=effectiveWCVG(W,L)

print("Length and width correction for intrinsic and overlap capacitances:")
display(Latex(f'$L =$ {L/1e-6:.3f} $\\mu m$'))
display(Latex(f'$L_{{CV}} =$ {Lcv/1e-6:.3f} $\\mu m$'))
display(Latex(f'$W =$ {W/1e-6:.3f} $\\mu m$'))
display(Latex(f'$W_{{CV}} =$ {Wcv/1e-6:.3f} $\\mu m$'))

print("Length and width correction for fringing capacitances:")
display(Latex(f'$L =$ {L/1e-6:.3f} $\\mu m$'))
display(Latex(f'$L_{{CVG}} =$ {Lcvg/1e-6:.3f} $\\mu m$'))
display(Latex(f'$W =$ {W/1e-6:.3f} $\\mu m$'))
display(Latex(f'$W_{{CVG}} =$ {Wcvg/1e-6:.3f} $\\mu m$'))

Length and width correction for intrinsic and overlap capacitances:


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Length and width correction for fringing capacitances:


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

In [5]:
# Since lvaro=0 and wvaro=0 we can set DeltaLPS=0 and DeltaLWOD=0. DLCVn and DWCVn are then simply given by
DLCVn=2*lap-dlq
DWCVn=2*wot-dwq

# Similarly for the fringing capacitances
DLGCVn=-dlq
DWGCVn=-dwq

print("Length and width correction for intrinsic and overlap capacitances:")
display(Latex(f'$\\Delta L_{{CV}} =$ {DLCVn/1e-9:.0f} nm'))
display(Latex(f'$\\Delta W_{{CV}} =$ {DWCVn/1e-9:.0f} nm'))

print("Length and width correction for fringing capacitances:")
display(Latex(f'$\\Delta L_{{G,CV}} =$ {DLGCVn/1e-9:.0f} nm'))
display(Latex(f'$\\Delta W_{{G,CV}} =$ {DWGCVn/1e-9:.0f} nm'))

Length and width correction for intrinsic and overlap capacitances:


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Length and width correction for fringing capacitances:


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

In [6]:
#| label: tbl-length_width_corrections
#| tbl-cap: Length and width corrections.

sekv_geom_param_df={
    "Length correction DL": [DLn, DLCVn, DLGCVn],
    "Width correction DW": [DWn, DWCVn, DWGCVn],
    "Comment": "extracted from PDK"
}
index_labels=["For current","For intrinsic and overlap capacitances","For fringing-field capacitances"]
sekv_geom_param_df=pd.DataFrame(sekv_geom_param_df, index=index_labels)
pd.set_option('display.float_format', '{:.3e}'.format)
sekv_geom_param_df

Length correction DL  \
For current                                        5.885e-08   
For intrinsic and overlap capacitances             7.257e-08   
For fringing-field capacitances                    1.372e-08   

                                        Width correction DW  \
For current                                      -2.000e-08   
For intrinsic and overlap capacitances           -1.000e-08   
For fringing-field capacitances                   1.000e-08   

                                                   Comment  
For current                             extracted from PDK  
For intrinsic and overlap capacitances  extracted from PDK  
For fringing-field capacitances         extracted from PDK

# Long-channel parameters

## DC Transfer Characteristic Parameters

### Generating the data

In [7]:
simulationPath="./Simulations/" + type + "/idgmvg/"
dataPath="./Data/" + type + "/"
fileName = "idgmvg"
dataFile = dataPath + fileName + "_" + type + "_long.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

W=10e-6
L=10e-6
Weff=effectiveW(W,L)
Leff=effectiveL(W,L)
VG=1
VS=0
VD=1.5

Npts=201
VGmin=-0.5
VGmax=1.5
dVG=(VGmax-VGmin)/(Npts-1)

if newSim:
    paramstr = '\n'.join((
        f'.param W={W/1e-6:.2f}u L={L/1e-6:.2f}u VG={VG:.1f} VS={VS:.1f} VD={VD:.1f}',
        f'.csparam VGmin = {VGmin:.3f}',
        f'.csparam VGmax = {VGmax:.3f}',
        f'.csparam dVG = {dVG:.3f}'
    ))
    #print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationPath + fileName + ".log", 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

### Importing and plotting the data

#### I~D~ and G~m~ versus V~G~

In [8]:
df_idgmvg=pd.read_table(dataFile, sep=' +', engine='python')
VG=df_idgmvg['v-sweep'].to_numpy()
ID=df_idgmvg['ID'].to_numpy()
Gm=df_idgmvg['Gm'].to_numpy()

Type='nMOS (t-t)'

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
mosinfo = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$',
    f'$V_S =$ {VS:.0f} V',
    f'$V_D =$ {VD:.1f} V'))
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VG, abs(Gm)/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_m|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [9]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
axs[0].text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$I_D$ [$\\mu A$]')
axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [10]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
axs[0].text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VG, sqrt(ID)/1e-3, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$\\sqrt{{I_D}}$ [$\\sqrt{{\\mu A}}$]')
axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 2400x900 with 2 Axes>

#### G~m~-V~G~

In [11]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
Gmnum=np.zeros(Npts)
dVG=VG[1]-VG[0]
Gmnum=diff(ID,dVG)

plt.semilogy(VG, abs(Gm)/1e-6,'ro', label='Data', markersize=msize, markevery=mevery)
plt.semilogy(VG, abs(Gmnum)/1e-6,'b-', label='Num. diff.')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_m$ [$\\mu A/V$]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

We see that the transconductance obtained by differentiating the large-signal $I_D$-$V_G$ characteristic is equal to the transconductance extracted from the PSP model. We will keep the value extracted from the PSP model.

#### G~m~-I~D~

In [12]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

plt.loglog(ID, Gm,'ro', label='Data', markersize=msize, markevery=mevery)
plt.loglog(ID, Gmnum,'b-', label='Num. diff.')
plt.xlabel('$I_D$ [A]')
#plt.xlim(1e-12,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
textstr = '\n'.join((
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$'))
plt.text(0.05, 0.95, mosinfo, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

#### Filtering the outliers

In [13]:
VGmini=-0.1
VGmaxi=1.5

VGsub=VG[(VG >= VGmini) & (VG <= VGmaxi)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
Gmsub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    Gmsub[k]=Gm[Nmin+k]

Nfil=Npts-Nsub
VGfil=np.zeros(Nfil)
IDfil=np.zeros(Nfil)
Gmfil=np.zeros(Nfil)

for k in range(0,Nfil):
    VGfil[k]=VG[k]
    IDfil[k]=ID[k]
    Gmfil[k]=Gm[k]

plt.semilogy(VGfil, IDfil, 'b-o', label='Outliers', markersize=msize, markevery=4)
plt.semilogy(VGsub ,IDsub, 'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$I_D$ [A]')
#plt.ylim(1e-12,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_ID_VG_outliers')
plt.show()

<Figure size 1200x900 with 1 Axes>

In [14]:
plt.semilogy(VGfil,abs(Gmfil),'b-o', label='Outliers', markersize=msize, markevery=2)
plt.semilogy(VGsub,abs(Gmsub),'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin, VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-10,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_Gm_VG_outliers')
plt.show()

<Figure size 1200x900 with 1 Axes>

In [15]:
plt.loglog(IDfil,Gmfil,'b-o', label='Outliers', markersize=msize, markevery=2)
plt.loglog(IDsub,Gmsub,'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$I_D$ [A]')
#plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-9,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

In [16]:
VG=VGsub
ID=IDsub
Gm=Gmsub

### Direct extraction with $\lambda_c=0$

#### Slope factor $n$ and $I_{spec}$ extraction

The gate transconductance in weak inversion and saturation is given by
\begin{equation}
  G_m = \frac{I_D}{n\,U_T}.
\end{equation}
So if we plot $I_D/(G_m\,U_T)$ we should see a plateau in weak inversion the value of which is equal to the slope factor $n$.

In [17]:
Npts=len(VG)
next=np.zeros(Npts)

for k in range(0,Npts):
    next[k]=ID[k]/(Gm[k]*UT)

nextmin=np.min(next)
Nmin=np.where(next == nextmin)[0]
IDext=ID[Nmin[0]]
n0=round(nextmin,2)
display(Latex(f'$n =$ {n0:.2f}'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-9:.2f} $nA$'))

plt.loglog(ID,next,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[n0,n0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1,n0],'k--', linewidth=lw)
plt.loglog(ID[Nmin],next[Nmin],'ko', markersize=msize)
plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.xlabel('$I_D$ [A]')
plt.ylim(1,1e2)
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate('$n =$' + f'{n0:.2f}', size=9,
             xy=(1e-10, n0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate('$I_D =$' + f'{IDext/1e-9:.2f} nA', size=9,
             xy=(IDext, 1), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_n_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

On the other hand the normalized $G_m/I_D$ function for a long-channel transistor in strong inversion and saturation is given by
\begin{equation}
  \frac{G_m\,n\,U_T}{I_D} = \frac{1}{\sqrt{IC}} = \sqrt{\frac{I_{spec}}{I_D}}.
\end{equation}
We can then plot $(G_m\,n\,U_T)^2/I_D$ which should find a maximum value equal to $I_{spec}$.

In [18]:
Ispecext=np.zeros(Npts)
nUT=n0*UT

for k in range(0,Npts):
    Ispecext[k]=(Gm[k]*nUT)**2/ID[k]

Ispec0=np.max(Ispecext)
Ispecsq0=Ispec0/(Weff/Leff)
Nmax=np.where(Ispecext == Ispec0)[0]
IDext=ID[Nmax[0]]
display(Latex(f'$W_{{eff}} =$ {Weff/1e-6:.3f} $\\mu m$'))
display(Latex(f'$L_{{eff}} =$ {Leff/1e-6:.3f} $\\mu m$'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-6:.3f} $\\mu A$'))

plt.loglog(ID,Ispecext,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[Ispec0,Ispec0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1e-12,Ispec0],'k--', linewidth=lw)
plt.loglog(ID[Nmax],Ispecext[Nmax],'ko', markersize=msize)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$(G_m\\,n\\,U_T)^2/I_D$ [A]')
plt.ylim(1e-10,1e-6)
plt.annotate(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} nA', size=9,
             xy=(1e-10, Ispec0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate('$I_D =$' + f'{IDext/1e-6:.2f} $\\mu A$', size=9,
             xy=(IDext, 1e-10), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}',
    f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq0/1e-9:.0f} nA'))
plt.text(0.5, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_Ispec_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

In [19]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))

Next=101
IDsi=np.linspace(Ispec0,1e-3,Next,endpoint=True)
IDGmUTsi=np.zeros(Next)

for k in range(0,Next):
    IDGmUTsi[k]=n*sqrt(IDsi[k]/Ispec)

plt.loglog(ID,next,'r-o', markersize=msize, markevery=2)
plt.loglog(IDsi,IDGmUTsi,'k--', linewidth=lw)
plt.loglog([1e-12,Ispec],[n,n],'k--', linewidth=lw)
plt.loglog([Ispec,Ispec],[1,n],'k--', linewidth=lw)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
plt.ylim(1,1e2)
plt.annotate(f'$n =$ {n:.2f}', size=9,
             xy=(1e-10, n), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA', size=9,
             xy=(Ispec, 1), xycoords='data',
             xytext=(50, 15), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='bottom')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_n_Ispec')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

Having extracted $n$ and $I_{spec}$, we can now plot the normalized $G_m/I_D$ function.

In [20]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
lambdac=0
Lsat=0
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e2],[1,1e-1],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_GmID_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is reasonable over the entire $IC$ span. There is some discrepancy in the moderate inversion region which is due to the mobility reduction due to the vertical field appearing for $IC >10^2$. The latter can be accounted for by using the $\lambda_c$ parameter which is normally used for modeling the effect of velocity saturation in short-channel transistor but can also be used to correct the effect of mobility reduction due to the vertical field appearing in long-channel transistors. We will not do this here since we want to extract the long-channel parameters keeping $\lambda_c=0$, but since we are mostly interested in the moderate inversion region, we can slightly increase $I_{spec}$ to improve the fit in moderate inversion at the cost of a degradation in strong inversion.

In [21]:
Ispecsq=810e-9
Ispec=Ispecsq*Weff/Leff
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e2],[1,1e-1],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_GmID_direct_modified')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is now much better in moderate inversion but less in strong inversion. This is due to mobility reduction due to the vertical field an effect that is not accounted for in the model. However, we will keep the new values.

#### Threshold voltage extraction

We can extract the threshold voltage in weak inversion (assuming $V_S=0$) from the normalized current (inversion coefficient) given by
\begin{equation}
  IC = e^{\frac{V_G-V_{T0}}{n U_T}}.
\end{equation}
We can now plot
\begin{equation}
  V_{T0} = V_G -n U_T \ln(IC)
\end{equation}
to extract the threshold voltage.

In [22]:
# We keep the initial values of n, Ispecsq and Ispec
#n=n0
#Ispecsq=Ispecsq0
#Ispec=Ispec0
# We keep the new values of n, Ispecsq and Ispec
n0=n
Ispecsq0=Ispecsq
Ispec0=Ispec
nUT=n*UT
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

ICsim=np.zeros(Npts)
VT0ext=np.zeros(Npts)

nUT=n0*UT

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    VT0ext[k]=VG[k]-nUT*ln(ICsim[k])

plt.plot(VG,VT0ext,'r-o', markersize=msize, markevery=mevery)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$V_{T0ext}$ [V]')
#plt.ylim(0,1.8)
#plt.yticks(np.arange(0,1.1,0.1))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}'))
plt.text(0.05, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We see a plateau in weak inversion where we can average its value to get the threshold voltage in weak inversion.

In [23]:
VGmin=-0.12
VGmax=0.15
VGsub=VG[(VG >= VGmin) & (VG <= VGmax)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

ICsub=np.zeros(Nsub)
VT0sub=np.zeros(Nsub)

for k in range(0,Nsub):
    ICsub[k]=ID[Nmin+k]/Ispec0
    VT0sub[k]=VGsub[k]-nUT*ln(ICsub[k])

VT0wi=np.mean(VT0sub)
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))

plt.plot(VGsub,VT0sub,'r-o', markersize=msize, markevery=1)
plt.plot([VGmin,VGmax],[VT0wi,VT0wi], 'k--')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$V_{T0ext}$ [V]')
plt.ylim(0,0.4)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate('$V_{{T0}} =$' + f'{VT0wi:.3f}', size=9,
             xy=(VGmin, VT0wi), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0wi/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}'))
plt.text(1.03, 0.5, textstr, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_average')
plt.show()

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The threshold voltage for this wide and long device is surprisingly small. It is in accordance with the documentation giving a typical-typical $V_{TH} \cong 200\,mV$ for $W=10\,\mu m$ and $L=10\,\mu m$.

We can now plot the $I_D$-$V_G$ for this threshold voltage.

In [24]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
VT0=VT0wi
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps(vps[k])
    idsim[k]=ID[k]/Ispec

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)
    
axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.4)
axs[0].set_xticks(np.arange(-0.4,1.6,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-4,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.4)
axs[1].set_xticks(np.arange(-0.4,1.6,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We get a reasonable fit with some deviations in the moderate inversion, which is expected since we fitted with the asymptotes.

We can also extract the threshold voltage in strong inversion.

In [25]:
# We keep the initial values of n, Ispecsq and Ispec
#n=n0
#Ispecsq=Ispecsq0
#Ispec=Ispec0
# We keep the new values of n, Ispecsq and Ispec
n0=n
Ispecsq0=Ispecsq
Ispec0=Ispec
nUT=n*UT
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

plt.plot(VG,sqrt(abs(ID)),'r-o', markersize=msize, markevery=mevery)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$\\sqrt{I_D}$ [$\\sqrt{A}$]')
#plt.ylim(0,1.8)
#plt.yticks(np.arange(0,1.1,0.1))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}'))
plt.text(0.05, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 1200x900 with 1 Axes>

In [26]:
from scipy.stats import linregress

VGmini=0.25
VGmaxi=1
VGsub=VG[(VG >= VGmini) & (VG <= VGmaxi)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
sqrtIDsub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    sqrtIDsub[k]=sqrt(abs(IDsub[k]))

slope, intercept, _, _, _ = linregress(VGsub, sqrtIDsub)
VT0si=-intercept/slope
display(Latex(f'$V_{{T0,si}}  =$ {VT0si/1e-3:.0f} mV'))

sqrtIDfit=np.zeros(Npts)

for k in range(0,Npts):
    sqrtIDfit[k]=slope*VG[k]+intercept

plt.plot(VG,sqrt(abs(ID)),'r-o', markersize=msize, markevery=mevery)
plt.plot(VG,sqrtIDfit,'b--')
plt.xlabel('$V_G$ [V]')
plt.xlim(0,VGmax)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$\\sqrt{I_D}$ [$\\sqrt{A}$]')
#plt.ylim(0,0.4)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0si/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}'))
plt.text(1.03, 0.5, textstr, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_average')
plt.show()

<IPython.core.display.Latex object>

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 1200x900 with 1 Axes>

We get a very small threshold voltage even smaller than the value extracted in weak inversion.

In [27]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
VT0=VT0si
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$V_{{T0,si}}  =$ {VT0si/1e-3:.0f} mV'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps(vps[k])
    idsim[k]=ID[k]/Ispec

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)
    
axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.4)
axs[0].set_xticks(np.arange(-0.4,1.6,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-4,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.4)
axs[1].set_xticks(np.arange(-0.4,1.6,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

As expected, we get a less good fit in weak inversion. We therefore keep the value of the threshold voltage extracted in weak inversion.

#### Summary

In [28]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
VT0=VT0wi
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
#ax1.set_ylim(1e-4,1e3)
ax1.set_yticks([1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e2)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.2)
#ax3.set_xticks(np.arange(-0.4,1.8,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,350)
ax3.set_yticks(np.arange(0,350,50))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_direct_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

In [29]:
#| label: tbl-long_sekv_parameters1
#| tbl-cap: Direct extraction of the sEKV parameters for the long-channel transistor with $\lambda_c=0$.

sekv_idvg_param_df={
    "W": [W],
    "Weff": [Weff],
    "L": [L],
    "Leff": [Leff],
    "n": [n],
    "Ispecsq": [Ispecsq],
    "VT0": [VT0],
    "lambdac": [lambdac],
    "Lsat": [Lsat],
    "Comment": "direct with lambdac=0"
}
index_labels=["long"]
sekv_idvg_param_df=pd.DataFrame(sekv_idvg_param_df, index=index_labels)
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   

      lambdac  Lsat                Comment  
long        0     0  direct with lambdac=0

### Extraction using optimization with $\lambda_c=0$

#### Slope factor $n$ and $I_{spec}$ extraction

We can try to extract $n$ and $I_{spec}$ for a long-channel directly from the normalized $G_m/I_d$ function.

In [30]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit1(ID,n,Ispec):
    IC=ID/Ispec
    gmsid=gmsid_ic(IC)
    nUT=n*UT
    return gmsid/nUT

Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

nini=n0
Ispecini=Ispec0
    
pars, cov = curve_fit(f=GmIDfit1, xdata=ID, ydata=GmIDsim, p0=[nini,Ispecini], )
n1=pars[0]
Ispec1=pars[1]
Ispecsq1=Ispec1/(Weff/Leff)

n=n1
Ispecsq=Ispecsq1
Ispec=Ispec1
nUT=n*UT
lambdac=0
Lsat=0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,sqrt(1e-3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We get a reasonable fit and values that similar to the direct extraction.

We can also try to keep the value of $n$ extracted from the direct extraction above and optimize for $I_{spec}$ only.

In [31]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit2(ID,Ispec):
    IC=ID/Ispec
    gmsid=gmsid_ic(IC)
    return gmsid/nUT

n=n0
nUT=n*UT
Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

Ispecini=Ispec0
pars, cov = curve_fit(f=GmIDfit2, xdata=ID, ydata=GmIDsim, p0=Ispecini)
Ispec2=pars[0]
Ispecsq2=Ispec2/(Weff/Leff)
lambdac=0

Ispecsq=Ispecsq2
Ispec=Ispec2
lambdac=0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,sqrt(1e-3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is good in weak and moderate inversion, but we still have some discrepancies in strong inversion which is due to mobility reduction due to the vertical field.
We will keep the last extracted values for $I_{specsq}$.

In [32]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

#### Threshold voltage extraction

In [33]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def logIDVGfit(VG,VT0):
    vps=(VG-VT0)/nUT
    IC=ic_vps(vps)
    return ln(IC)

idsim=np.zeros(Npts)
logidsim=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    logidsim[k]=ln(idsim[k])

nUT=n*UT
VT0ini=0.4

pars, cov = curve_fit(f=logIDVGfit, xdata=VG, ydata=logidsim, p0=VT0ini)
VT04=pars[0]

VT0=VT04

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)

VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)

axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.4)
axs[0].set_xticks(np.arange(-0.4,1.6,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-4,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.4)
axs[1].set_xticks(np.arange(-0.4,1.6,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

#saveFigures(savePath, 'ext_param_vs_length')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We see a reasonable fit except in strong inversion. This is expected since we optimized the moderate inversion region.

#### Summary

In [34]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
ax1.set_ylim(1e-4,1e3)
ax1.set_yticks([1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e2)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.4)
ax3.set_xticks(np.arange(-0.4,1.6,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,500)
ax3.set_yticks(np.arange(0,500,100))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_opt_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

The extraction using curve-fitting gives a better fit in moderate inversion but less in strong inversion.

In [35]:
#| label: tbl-long_sekv_parameters2
#| tbl-cap: Extraction of the sEKV parameters by optimization for the long-channel transistor with $\lambda_c=0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"optimization with lambdac=0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={1: "long"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   

      lambdac  Lsat                      Comment  
long        0     0        direct with lambdac=0  
long        0     0  optimization with lambdac=0

### Extraction using optimization with $\lambda_c > 0$

We start extracting $n$, $I_{spec}$ and $\lambda_c$ using curve fitting on $G_m/I_D$.

In [36]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit4(ID,n,Ispec,lambdac):
    nUT=n*UT
    IC=ID/Ispec
    gmsid=gmsid_ic_short(IC,lambdac)
    return gmsid/nUT

Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

nini=n0
Ispecini=Ispec0
lambdacini=0.1

pars, cov = curve_fit(f=GmIDfit4, xdata=ID, ydata=GmIDsim, p0=[nini,Ispecini,lambdacini], )
n4=pars[0]
Ispec4=pars[1]
lambdac4=pars[2]
Ispecsq4=Ispec4*L/W

n=n4
Ispecsq=Ispecsq4
Ispec=Ispec4
lambdac=lambdac4
Lsat=lambdac*Leff

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} nm'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, 'CS_OL_ib_vs_IC_GBW_Adc_no_VS')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We now have a good fit in strong inversion that we can still improve by slightly reducing the value of $I_{specsq}$, which seems too high and $\lambda_c$.

In [37]:
n=n4
Ispecsq=850e-9
Ispec=Ispecsq*Weff/Leff
lambdac=0.055
Lsat=lambdac*Leff

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We now have an almost perfect fit.

#### Summary

We can now check the large and small-signal characteristics.

In [38]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
ax1.set_ylim(1e-4,1e3)
ax1.set_yticks([1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e2)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.4)
ax3.set_xticks(np.arange(-0.4,1.6,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,)
ax3.set_yticks(np.arange(0,500,100))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_with_lambdac_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

In [39]:
#| label: tbl-long_sekv_parameters3
#| tbl-cap: Extraction of the sEKV parameters by optimization for the long-channel transistor with $\lambda_c>0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"optimization with lambdac>0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={2: "long"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.272e+00 8.500e-07 1.733e-01   

       lambdac      Lsat                      Comment  
long 0.000e+00 0.000e+00        direct with lambdac=0  
long 0.000e+00 0.000e+00  optimization with lambdac=0  
long 5.500e-02 5.468e-07  optimization with lambdac>0

## Output characteristic

### Generating the data

In [40]:
simulationPath="./Simulations/" + type + "/idgdsvd/"
dataPath="./Data/" + type + "/"
fileName = "idgdsvd"
dataFile = dataPath + fileName + "_" + type + "_long.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

VS=0
VD=1.2

idx=1
n=sekv_idvg_param_df.iloc[idx]['n']
Ispecsq=sekv_idvg_param_df.iloc[idx]['Ispecsq']
VT0=sekv_idvg_param_df.iloc[idx]['VT0']

#n=1.21
#VT0=173e-3
#Ispecsq=825e-9
IC=1
Ispec=Ispecsq*Weff/Leff
ID=Ispec*IC
vps=vps_ic(IC)
nUT=n*UT
VG=VT0+nUT*vps

Npts=201
VDmin=0
VDmax=1.2
dVD=(VDmax-VDmin)/(Npts-1)

if newSim:
    paramstr = '\n'.join((
        f'.param W={W/1e-6:.2f}u L={L/1e-6:.2f}u VG={VG:.1f} VS={VS:.1f} VD={VD:.1f}',
        f'.csparam VDmin = {VDmin:.3f}',
        f'.csparam VDmax = {VDmax:.3f}',
        f'.csparam dVD = {dVD:.3f}'
    ))
    #print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationPath + fileName + ".log", 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

### Importing and plotting the data

#### I~D~ and G~ds~ versus V~D~

In [41]:
df_idgdsvd=pd.read_table(dataFile, sep=' +', engine='python')
VD=df_idgdsvd['v-sweep'].to_numpy()
ID=df_idgdsvd['ID'].to_numpy()
Gds=df_idgdsvd['Gds'].to_numpy()

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].plot(VD, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
mosinfo = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$',
    f'$V_S =$ {VS:.0f} V',
    f'$IC \\cong$ {IC:.0f}',
    f'$V_G =$ {VG/1e-3:.0f} mV'))
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VD, abs(Gds)/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [42]:
Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]
Gdsnum=np.zeros(Npts)
dVD=VD[1]-VD[0]
Gdsnum=diff(ID,dVD)

plt.semilogy(VD, Gds/1e-6,'ro', label='Data', markersize=msize, markevery=mevery)
plt.semilogy(VD, Gdsnum/1e-6,'b-', label='Num. diff.')
plt.xlabel('$V_D$ [V]')
plt.xlim(VDmin,VDmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_{ds}$ [$\\mu A/V$]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower left')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

The output conductance calculated by differentiating the large-signal $I_D$-$V_D$ matches the value extracted from the PSP model. We will keep the value from PSP.

#### Filtering the outliers

In [43]:
VDmini=0.16
VDmaxi=1.2

VDsub=VD[(VD >= VDmini) & (VD <= VDmaxi)]
Nsub=len(VDsub)
Nmin=np.where(VD == VDsub[0])[0][0]
Nmax=np.where(VD == VDsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
Gdssub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    Gdssub[k]=Gds[Nmin+k]

Nfil=Npts-Nsub
VDfil=np.zeros(Nfil)
IDfil=np.zeros(Nfil)
Gdsfil=np.zeros(Nfil)

for k in range(0,Nfil):
    VDfil[k]=VD[k]
    IDfil[k]=ID[k]
    Gdsfil[k]=Gds[k]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)

axs[0].plot(VDfil, IDfil/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[0].plot(VDsub, IDsub/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VDfil, abs(Gdsfil)/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[1].semilogy(VDsub, abs(Gdssub)/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

### Extracting the CLM parameter

In [44]:
from scipy.stats import linregress

slope, intercept, _, _, _ = linregress(VDsub, IDsub)
Gdsext=slope
ID0ext=intercept
VEext=-ID0ext/Gdsext
lambdaext=-VEext/L

display(Latex(f'$G_{{ds}} =$ {Gdsext/1e-6:.3f} $\\mu A/V$'))
display(Latex(f'$I_{{D0}} =$ {ID0ext/1e-6:.3f} $\\mu A$'))
display(Latex(f'$V_E =$ {VEext:.3f} $V$'))
display(Latex(f'$\\lambda =$ {lambdaext/1e6:.3f} $V/\\mu m$'))

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]

IDfit=np.zeros(Npts)
Gdsfit=np.zeros(Npts)

for k in range(0,Npts):
#    IDfit[k]=ID0ext+Gdsext*VD[k]
    IDfit[k]=Gdsext*(VD[k]-VEext)
    Gdsfit[k]=Gdsext

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)

axs[0].plot(VDfil, IDfil/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[0].plot(VDsub, IDsub/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[0].plot(VD, IDfit/1e-6, 'k--', label='Fit')
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,1.6,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
#axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
textstr1 = '\n'.join((
    f'$I_{{D0}} =$ {ID0ext/1e-6:.3f} $\\mu A$',
    f'$G_{{ds}} =$ {Gdsext/1e-6:.3f} $\\mu A/V$',
    f'$V_E =$ {VEext:.3f} V',
    f'$\\lambda =$ {lambdaext/1e6:.3f} $V/\\mu m$'))
axs[0].text(0.6, 0.05, textstr1, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VDfil, abs(Gdsfil)/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[1].semilogy(VDsub, abs(Gdssub)/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[1].semilogy(VD, Gdsfit/1e-6, 'k--', label='Fit')
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2400x900 with 2 Axes>

We get a rather high output conductance and hence low value of the $\lambda$ parameter for such a long transistor.

In [45]:
#| label: tbl-long_clm_parameters1
#| tbl-cap: CLM parameters extracted for the long-channel transistor in moderate inversion.

sekv_idvd_param_df={
    "W": [W],
    "Weff": [Weff],
    "L": [L],
    "Leff": [Leff],
    "IC": [IC],
    "Gds": [Gdsext],
    "ID0": [ID0ext],
    "VE": [VEext],
    "lambda": [lambdaext],
    "Comment": "moderate"
}
index_labels=["long"]
sekv_idvd_param_df=pd.DataFrame(sekv_idvd_param_df, index=index_labels)
sekv_idvd_param_df

W      Weff         L      Leff  IC       Gds       ID0  \
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06   1 2.105e-07 6.119e-07   

             VE    lambda   Comment  
long -2.907e+00 2.907e+05  moderate

## Noise

In this section we will extract the flicker noise parameters to be used with sEKV and check the white noise power spectral desnity (PSD). We reuse the flicker noise model from EKV 2.6, where the input (gate) referred PSD is given by

\begin{equation}
  S_{nin,fl}(f) = \frac{KF}{W_{eff}\,L_{eff}\,C_{ox}\; f^{AF}}
\end{equation}

In this model the flicker noise is assumed to scale as $1/C_{ox}$, which is correct if the noise follows the the Hooge model (i.e. originates from mobility fluctuations). In the case of the Mc Worther model (i.e. flicker noise originating from traps in Si-SiO~2~ interface and in the oxyde), the PSD scales as $C_{ox}^2$. Despiet the flicker noise is usually domanted by the trapping mechanism, we will keep the above model with a $1/C_{ox}$ scaling.

In EKV , we like to rewrite the flicker noise PSD like the thermal noise in terms of a input-referred noise resistance

\begin{equation}
  S_{nin,fl}(f) = 4 kT\,R_{nin,fl}(f)
\end{equation}

where

\begin{equation}
  R_{nin,fl}(f) = \frac{\rho}{W_{eff}\,L_{eff}\,f^{AF}}
\end{equation}

with

\begin{equation}
  \rho = \frac{KF}{4 kT\,C_{ox}}
\end{equation}

Note that the flicker noise parameter have some weird units. Indeed, $KF$ is in $A \cdot V \cdot s^{2-AF}$ and $\rho$ is in $V \cdot m^2 / (A \cdot s^{AF})$. If $AF = 1$, like it is often the case, then $KF$ is in $A \cdot V \cdot s$ and $\rho$ is in $V \cdot m^2 / (A \cdot s)$.

To extract the noise parameters, we use a common-source stage loaded by a noiseless resistor. We first will set the bias condition in terms of $IC$ and calculate the input-referred white noise to compare it to the result obtained from the PSP simulations.

### Setting bias conditions

Having extracted $n$, $I_{spec\Box}$ and $V_{T0}$, we can impose the inversion coefficient and calculate the corresponding gate voltage $V_G$. We nee to make sure the transistor remains in saturation.

In [46]:
#n=1.21
#VT0=173e-3
#Ispecsq=825e-9
tox=2.2404e-09
Cox=epsilonox*epsilon0/tox
idx=1
n=sekv_idvg_param_df.iloc[idx]['n']
sekv_idvg_param_df.iloc[idx]['Ispecsq']
VT0=sekv_idvg_param_df.iloc[idx]['VT0']

VDD=1.2
IC=1
Ispec=Ispecsq*Weff/Leff
ID=Ispec*IC
#qs=q_ic(IC)
vps=vps_ic(IC)
nUT=n*UT
VG=VT0+nUT*vps
VS=0
gms=gms_ic(IC)
Gmekv=Ispec/nUT*gms
gammanekv=gamman_ic(IC,n)
Rnthekv=gammanekv/Gmekv
Snthekv=4*kT*Rnthekv
Vnthekv0=sqrt(Snthekv)
Av=10
RL=Av/Gmekv
VRL=ID*RL
VDS=VDD-VRL
VDSsat=UT*vdssat_ic(IC)
region="saturation" if VDS > VDSsat else "linear"

display(Latex(f'$W =$ {W/1e-6:.0f} $\\mu m$'))
display(Latex(f'$L =$ {L/1e-6:.0f} $\\mu m$'))
display(Latex(f'$IC =$ {IC:.0f}'))
display(Latex(f'$I_{{D}} =$ {ID/1e-6:.3f} $\\mu A$'))
display(Latex(f'$V_{{G}} =$ {VG:.3f} $V$'))
display(Latex(f'$V_{{S}} =$ {VS:.3f} $V$'))
display(Latex(f'$G_{{m}} =$ {Gmekv/1e-6:.3f} $\\mu A/V$'))
display(Latex(f'$\\gamma_n =$ {gammanekv:.3f}'))
display(Latex(f'$R_{{n,th}} =$ {Rnthekv/1e3:.3f} $k \\Omega$'))
display(Latex(f'$S_{{n,th}} =$ {Snthekv:.3e} $V^2/Hz$'))
display(Latex(f'$V_{{n,th}} =$ {Vnthekv0/1e-9:.3f} $nV/\\sqrt{{Hz}}$'))
display(Latex(f'$A_v =$ {Av:.0f}'))
display(Latex(f'$R_L =$ {RL/1e3:.3f} $k \\Omega$'))
display(Latex(f'$V_{{DD}} =$ {VDD:.3f} $V$'))
display(Latex(f'$V_{{RL}} =$ {VRL:.3f} $V$'))
display(Latex(f'$V_{{DS}} =$ {VDS:.3f} $V$'))
display(Latex(f'$V_{{DSsat}} =$ {VDSsat:.3f} $V$'))
print(f'The transistor is biased in the {region} region')

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

...

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

The transistor is biased in the saturation region


### Extract operating point information

In [47]:
simulationPath="./Simulations/" + type + "/noise/"
dataPath="./Data/" + type + "/"
fileName = "noise"
dataFile = dataPath + fileName + "_" + type + "_long.op.dat"
opFile = simulationPath + fileName + ".op.dat"
paramFile = simulationPath + fileName + ".op.par"
simulationFile = simulationPath + fileName + ".op.cir"
simulationLog = simulationPath + fileName + ".op.log"
simulationData = simulationPath + fileName + ".op.dat"

if newSim:
    paramstr = '\n'.join((
        f'.param VDD={VDD:.1f} VG={VG:.3f} RL={RL/1e3:.3f}k',
        f'.param W={W/1e-6:.0f}u L={L/1e-6:.0f}u'
    ))
    print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationLog, 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

We can extract the values of the PSP noise parameters from the operating point informations.

In [48]:
mosop_df=pd.read_table(dataFile, sep=r'\s+', dtype=np.float64, engine='python')
mosop_df=mosop_df.rename(columns={'@n.xn.nsg13_lv_nmos[weff]': 'Transistor',
                              '@n.xn.Nsg13_lv_nmos[weff]': 'Weff',
                              '@n.xn.Nsg13_lv_nmos[leff]': 'Leff',
                              '@n.xn.Nsg13_lv_nmos[ids]': 'IDS',
                              '@n.xn.Nsg13_lv_nmos[gm]': 'Gm',
                              '@n.xn.Nsg13_lv_nmos[gds]': 'Gds',
                              '@n.xn.Nsg13_lv_nmos[sid]': 'Snidth',
                              '@n.xn.Nsg13_lv_nmos[sqrtsfw]': 'Vninth',
                              '@n.xn.Nsg13_lv_nmos[sfl]': 'Snidfl @ 1Hz',
                              '@n.xn.Nsg13_lv_nmos[sqrtsff]': 'Vninfl @ 1kHz',
                              '@n.xn.Nsg13_lv_nmos[fknee]': 'fk'
                    })
mosop_df['Transistor'] = mosop_df['Transistor'].astype(str)
mosop_df.at[0, 'Transistor'] = 'Mn'
mosop_df.set_index('Transistor', inplace=True)
mosop_df.rename_axis(index=None, inplace=True)

Weffpsp=mosop_df.at['Mn','Weff']
Leffpsp=mosop_df.at['Mn','Leff']
Gmpsp=mosop_df.at['Mn','Gm']
Snidthpsp=mosop_df.at['Mn','Snidth']
Snidfl1Hzpsp=mosop_df.at['Mn','Snidfl @ 1Hz']
Snthpsp=Snidthpsp/Gmpsp**2
Vnthpsp0=mosop_df.at['Mn','Vninth']
Snfl1Hzpsp=Snidfl1Hzpsp/Gmpsp**2
Vnfl1Hzpsp=sqrt(Snfl1Hzpsp)
Vnfl1kHzpsp=mosop_df.at['Mn','Vninfl @ 1kHz']
KFpsp=Snfl1Hzpsp*Weffpsp*Leffpsp*Cox # Definition from EKV 2.6
KFlong=KFpsp
rhopsp=KFpsp/(4*kT*Cox)
rholong=rhopsp
AFpsp=log(Snfl1Hzpsp/Vnfl1kHzpsp**2)/3
fkpsp=mosop_df.at['Mn','fk']
Rnthpsp=Snthpsp/(4*kT)
gammanpsp=Gmpsp*Rnthpsp

display(Latex(f'$V_{{n,th}} =$ {Vnthpsp0/1e-9:.3f} $nV/\\sqrt{{Hz}}$ (PSP)'))
display(Latex(f'$f_k=$ {fkpsp/1e3:.3f} $kHz$ (PSP)'))
display(Latex(f'$KF =$ {KFpsp:.3e} $V A s$ (PSP)'))
display(Latex(f'$\\rho =$ {rhopsp:.3f} $V m^2/(A s)$ (PSP)'))
display(Latex(f'$AF =$ {AFpsp:.3f} (PSP)'))
display(Latex(f'$R_{{n,th}} =$ {Rnthpsp/1e3:.3f} $k \\Omega$ (PSP)'))
display(Latex(f'$\\gamma_n =$ {gammanpsp:.3f} (PSP)'))

mosop_df

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Weff      Leff       IDS        Gm       Gds    Snidth    Vninth  \
Mn 1.002e-05 9.941e-06 7.304e-07 1.490e-05 1.858e-07 1.742e-25 2.801e-08   

    Snidfl @ 1Hz  Vninfl @ 1kHz        fk  
Mn     4.593e-22      4.548e-08 2.637e+03

### Simulating noise PSD

We can now simulate the PSD and check against the EKV model.

In [49]:
simulationPath="./Simulations/" + type + "/noise/"
dataPath="./Data/" + type + "/"
fileName = "noise"
dataFile = dataPath + fileName + "_" + type + "_long.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

fmin=1
fmax=1e8
decPts=21

if newSim:
    paramstr = '\n'.join((
        f'.param VDD={VDD:.1f} VG={VG:.3f} RL={RL/1e3:.0f}k',
        f'.param W={W/1e-6:.0f}u L={L/1e-6:.0f}u',
        f'.csparam fmin = {fmin:.0e}',
        f'.csparam fmax = {fmax:.0e}',
        f'.csparam decPts = {decPts:.0f}'
    ))
    print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationLog, 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

In [50]:
df_noise=pd.read_table(dataFile, sep=' +', engine='python')
freq=df_noise['frequency'].to_numpy()
Vninpsp=df_noise['inoise_spectrum'].to_numpy()
Vnoutpsp=df_noise['onoise_spectrum'].to_numpy()

Npts=len(freq)
fmin=freq[0]
fmax=freq[Npts-1]

Vnthekv=np.zeros(Npts)
Snflekv=np.zeros(Npts)
Vnflekv=np.zeros(Npts)

for k in range(0,Npts):
    Vnthekv[k]=Vnthekv0
    Snflekv[k]=KFpsp/(Weff*Leff*Cox*freq[k])
    Vnflekv[k]=sqrt(Snflekv[k])

plt.loglog(freq, Vnoutpsp,'r-', label='Output noise (PSP)')
plt.loglog(freq, Vninpsp,'b-', label='Input noise (PSP)')
plt.loglog(freq, Vnthekv,'k--', label='White input noise (sEKV)')
plt.loglog(freq, Vnflekv,'k-.', label='Flicker input noise (model)')
#plt.loglog([fk,fk],[1e-10,Vnth],'k--')
plt.xlim(fmin,fmax)
#plt.xticks([1e0,1e1,1e2,1e3,1e4,1e5,1e6,1e7,1e8,1e9])
plt.xlabel('Frequency [Hz]')
plt.ylim(1e-9,1e-5)
plt.ylabel('$\\sqrt{S_{nout}}$ and $\\sqrt{S_{nin}}$ $[V/\\sqrt{Hz}]$')
plt.legend(loc='lower left', fontsize=9)
#plt.legend(loc='center left', fontsize=9, bbox_to_anchor=(1, 0.5))
textstr1 = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$'))
textstr2 = '\n'.join((
    f'$IC =$ {IC:.0f}',
    f'$V_G =$ {VG:.3f} V',
    f'$V_{{DS}} =$ {VDS:.3f} V',
    f'$R_L =$ {RL/1e3:.1f} $k\\Omega$'))
textstr3 = '\n'.join((
    f'$G_m =$ {Gmpsp/1e-6:.3f} $\\mu A/V$ (PSP)',
    f'$G_m =$ {Gmekv/1e-6:.3f} $\\mu A/V$ (EKV)',
    f'$\\sqrt{{S_{{in,th}}}} =$ {Vnthpsp0:.3e} (PSP)',
    f'$\\sqrt{{S_{{in,th}}}} =$ {Vnthekv0:.3e} (EKV)',
#    f'$R_{{n,th}} =$ {Rnthpsp/1e3:.3f} $k\\Omega$ (PSP)',
#    f'$R_{{n,th}} =$ {Rnthekv/1e3:.3f} $k\\Omega$ (EKV)',
    f'$\\gamma_n =$ {gammanpsp:.3f} (PSP)',
    f'$\\gamma_n =$ {gammanekv:.3f} (EKV)',
    f'$KF =$ {KFpsp:.3e} $V A s$ (PSP)',
    f'$\\rho =$ {rhopsp:.3e} $V m^2/(A s)$ (PSP)',
    f'$AF =$ {AFpsp:.3f} (PSP)',
    f'$f_k =$ {fkpsp/1e3:.3f} kHz (PSP)'))
plt.text(0.4, 0.95, textstr1, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.text(0.7, 0.95, textstr2, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.text(1.05, 0.5, textstr3, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#plt.text(fk, 1e-9, '$f_k =$'+f'{fk/1e3:.0f} kHz', ha='left', va='bottom', size=14)
#plt.text(1e2, Vnth, '$\sqrt{S_{nin,th}} =$'+f'{Vnth/1e-9:.1f} '+'$nV/\sqrt{Hz}$', ha='center', va='bottom', size=14)
#saveFigures(savePath, 'Input_referred_noise_PSD')
plt.show()

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 1200x900 with 1 Axes>

The flicker noise parameters are given by

In [51]:
#| label: tbl-long_noise_parameters
#| tbl-cap: Extraction of the noise parameters for the long-channel transistor.

KFn=KFpsp
rhon=rhopsp
AFn=AFpsp

sekv_noise_param_df={
    "W": [W],
    "Weff": [Weff],
    "L": [L],
    "Leff": [Leff],
    "IC": [IC],
    "KF": [KFn],
    "AF": [AFn],
    "rho": [rhon],
    "Comment": "moderate"
}
index_labels=["long"]
sekv_noise_param_df=pd.DataFrame(sekv_noise_param_df, index=index_labels)
sekv_noise_param_df

W      Weff         L      Leff  IC        KF        AF  \
long 1.000e-05 1.002e-05 1.000e-05 9.941e-06   1 3.175e-24 1.000e+00   

           rho   Comment  
long 1.243e-02  moderate

# Medium-channel parameters

## DC Transfer Characteristic Parameters

### Generating the data

In [52]:
simulationPath="./Simulations/" + type + "/idgmvg/"
dataPath="./Data/" + type + "/"
fileName = "idgmvg"
dataFile = dataPath + fileName + "_" + type + "_medium.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

W=1e-6
L=1e-6
Weff=effectiveW(W,L)
Leff=effectiveL(W,L)
VG=1
VS=0
VD=1.5

Npts=201
VGmin=-0.5
VGmax=1.5
dVG=(VGmax-VGmin)/(Npts-1)

if newSim:
    paramstr = '\n'.join((
        f'.param W={W/1e-6:.2f}u L={L/1e-6:.2f}u VG={VG:.1f} VS={VS:.1f} VD={VD:.1f}',
        f'.csparam VGmin = {VGmin:.3f}',
        f'.csparam VGmax = {VGmax:.3f}',
        f'.csparam dVG = {dVG:.3f}'
    ))
    #print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationPath + fileName + ".log", 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

### Importing and plotting the data

#### I~D~ and G~m~ versus V~G~

In [53]:
df_idgmvg=pd.read_table(dataFile, sep=' +', engine='python')
VG=df_idgmvg['v-sweep'].to_numpy()
ID=df_idgmvg['ID'].to_numpy()
Gm=df_idgmvg['Gm'].to_numpy()

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
mosinfo = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$',
    f'$V_S =$ {VS:.0f} V',
    f'$V_D =$ {VD:.1f} V'))
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VG, abs(Gm)/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_m|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [54]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
axs[0].text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$I_D$ [$\\mu A$]')
axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [55]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
axs[0].text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VG, sqrt(ID)/1e-3, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$\\sqrt{{I_D}}$ [$\\sqrt{{\\mu A}}$]')
axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 2400x900 with 2 Axes>

#### G~m~-V~G~

In [56]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
Gmnum=np.zeros(Npts)
dVG=VG[1]-VG[0]
Gmnum=diff(ID,dVG)

plt.semilogy(VG, abs(Gm)/1e-6,'ro', label='Data', markersize=msize, markevery=mevery)
plt.semilogy(VG, abs(Gmnum)/1e-6,'b-', label='Num. diff.')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_m$ [$\\mu A/V$]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

We see that the transconductance obtained by differentiating the large-signal $I_D$-$V_G$ characteristic is equal to the transconductance extracted from the PSP model. We will keep the value extracted from the PSP model.

#### G~m~-I~D~

In [57]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

plt.loglog(ID, Gm,'ro', label='Data', markersize=msize, markevery=mevery)
plt.loglog(ID, Gmnum,'b-', label='Num. diff.')
plt.xlabel('$I_D$ [A]')
#plt.xlim(1e-12,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
textstr = '\n'.join((
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$'))
plt.text(0.05, 0.95, mosinfo, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

#### Filtering the outliers

In [58]:
VGmini=-0.1
VGmaxi=1.5

VGsub=VG[(VG >= VGmini) & (VG <= VGmaxi)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
Gmsub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    Gmsub[k]=Gm[Nmin+k]

Nfil=Npts-Nsub
VGfil=np.zeros(Nfil)
IDfil=np.zeros(Nfil)
Gmfil=np.zeros(Nfil)

for k in range(0,Nfil):
    VGfil[k]=VG[k]
    IDfil[k]=ID[k]
    Gmfil[k]=Gm[k]

plt.semilogy(VGfil, IDfil, 'b-o', label='Outliers', markersize=msize, markevery=4)
plt.semilogy(VGsub ,IDsub, 'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$I_D$ [A]')
#plt.ylim(1e-12,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_ID_VG_outliers')
plt.show()

<Figure size 1200x900 with 1 Axes>

In [59]:
plt.semilogy(VGfil,abs(Gmfil),'b-o', label='Outliers', markersize=msize, markevery=2)
plt.semilogy(VGsub,abs(Gmsub),'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin, VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-10,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_Gm_VG_outliers')
plt.show()

<Figure size 1200x900 with 1 Axes>

In [60]:
plt.loglog(IDfil,Gmfil,'b-o', label='Outliers', markersize=msize, markevery=2)
plt.loglog(IDsub,Gmsub,'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$I_D$ [A]')
#plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-9,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

In [61]:
VG=VGsub
ID=IDsub
Gm=Gmsub

### Direct extraction with $\lambda_c=0$

#### Slope factor $n$ and $I_{spec}$ extraction

The gate transconductance in weak inversion and saturation is given by
\begin{equation}
  G_m = \frac{I_D}{n\,U_T}.
\end{equation}
So if we plot $I_D/(G_m\,U_T)$ we should see a plateau in weak inversion the value of which is equal to the slope factor $n$.

In [62]:
Npts=len(VG)
next=np.zeros(Npts)

for k in range(0,Npts):
    next[k]=ID[k]/(Gm[k]*UT)

nextmin=np.min(next)
Nmin=np.where(next == nextmin)[0]
IDext=ID[Nmin[0]]
n0=round(nextmin,2)
display(Latex(f'$n =$ {n0:.2f}'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-9:.2f} $nA$'))

plt.loglog(ID,next,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[n0,n0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1,n0],'k--', linewidth=lw)
plt.loglog(ID[Nmin],next[Nmin],'ko', markersize=msize)
plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.xlabel('$I_D$ [A]')
plt.ylim(1,1e2)
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate('$n =$' + f'{n0:.2f}', size=9,
             xy=(1e-10, n0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate('$I_D =$' + f'{IDext/1e-9:.2f} nA', size=9,
             xy=(IDext, 1), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_n_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

On the other hand the normalized $G_m/I_D$ function for a long-channel transistor in strong inversion and saturation is given by
\begin{equation}
  \frac{G_m\,n\,U_T}{I_D} = \frac{1}{\sqrt{IC}} = \sqrt{\frac{I_{spec}}{I_D}}.
\end{equation}
We can then plot $(G_m\,n\,U_T)^2/I_D$ which should find a maximum value equal to $I_{spec}$.

In [63]:
Ispecext=np.zeros(Npts)
nUT=n0*UT

for k in range(0,Npts):
    Ispecext[k]=(Gm[k]*nUT)**2/ID[k]

Ispec0=np.max(Ispecext)
Ispecsq0=Ispec0/(Weff/Leff)
Nmax=np.where(Ispecext == Ispec0)[0]
IDext=ID[Nmax[0]]
display(Latex(f'$W_{{eff}} =$ {Weff/1e-6:.3f} $\\mu m$'))
display(Latex(f'$L_{{eff}} =$ {Leff/1e-6:.3f} $\\mu m$'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-6:.3f} $\\mu A$'))

plt.loglog(ID,Ispecext,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[Ispec0,Ispec0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1e-12,Ispec0],'k--', linewidth=lw)
plt.loglog(ID[Nmax],Ispecext[Nmax],'ko', markersize=msize)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$(G_m\\,n\\,U_T)^2/I_D$ [A]')
plt.ylim(1e-10,1e-6)
plt.annotate(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} nA', size=9,
             xy=(1e-10, Ispec0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate('$I_D =$' + f'{IDext/1e-6:.2f} $\\mu A$', size=9,
             xy=(IDext, 1e-10), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}',
    f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq0/1e-9:.0f} nA'))
plt.text(0.5, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_Ispec_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

In [64]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))

Next=101
IDsi=np.linspace(Ispec0,1e-3,Next,endpoint=True)
IDGmUTsi=np.zeros(Next)

for k in range(0,Next):
    IDGmUTsi[k]=n*sqrt(IDsi[k]/Ispec)

plt.loglog(ID,next,'r-o', markersize=msize, markevery=2)
plt.loglog(IDsi,IDGmUTsi,'k--', linewidth=lw)
plt.loglog([1e-12,Ispec],[n,n],'k--', linewidth=lw)
plt.loglog([Ispec,Ispec],[1,n],'k--', linewidth=lw)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
plt.ylim(1,1e2)
plt.annotate(f'$n =$ {n:.2f}', size=9,
             xy=(1e-10, n), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA', size=9,
             xy=(Ispec, 1), xycoords='data',
             xytext=(50, 15), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='bottom')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_n_Ispec')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

Having extracted $n$ and $I_{spec}$, we can now plot the normalized $G_m/I_D$ function.

In [65]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
lambdac=0
Lsat=0
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e2],[1,1e-1],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_GmID_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is reasonable over the entire $IC$ span. There is some discrepancy in the moderate inversion region which is due to the mobility reduction due to the vertical field appearing for $IC >10^2$. The latter can be accounted for by using the $\lambda_c$ parameter which is normally used for modeling the effect of velocity saturation in short-channel transistor but can also be used to correct the effect of mobility reduction due to the vertical field appearing in long-channel transistors. We will not do this here since we want to extract the long-channel parameters keeping $\lambda_c=0$, but since we are mostly interested in the moderate inversion region, we can slightly increase $I_{spec}$ to improve the fit in moderate inversion at the cost of a degradation in strong inversion.

In [66]:
Ispecsq=650e-9
Ispec=Ispecsq*Weff/Leff
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e2],[1,1e-1],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_GmID_direct_modified')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is now much better in moderate inversion but less in strong inversion. This is due to mobility reduction due to the vertical field an effect that is not accounted for in the model. However, we will keep the new values.

#### Threshold voltage extraction

We can extract the threshold voltage in weak inversion (assuming $V_S=0$) from the normalized current (inversion coefficient) given by
\begin{equation}
  IC = e^{\frac{V_G-V_{T0}}{n U_T}}.
\end{equation}
We can now plot
\begin{equation}
  V_{T0} = V_G -n U_T \ln(IC)
\end{equation}
to extract the threshold voltage.

In [67]:
# We keep the initial values of n, Ispecsq and Ispec
#n=n0
#Ispecsq=Ispecsq0
#Ispec=Ispec0
# We keep the new values of n, Ispecsq and Ispec
n0=n
Ispecsq0=Ispecsq
Ispec0=Ispec
nUT=n*UT

display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

ICsim=np.zeros(Npts)
VT0ext=np.zeros(Npts)

nUT=n0*UT

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    VT0ext[k]=VG[k]-nUT*ln(ICsim[k])

plt.plot(VG,VT0ext,'r-o', markersize=msize, markevery=mevery)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$V_{T0ext}$ [V]')
#plt.ylim(0,1.8)
#plt.yticks(np.arange(0,1.1,0.1))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.05, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We see a plateau in weak inversion where we can average its value to get the threshold voltage in weak inversion.

In [68]:
VGmin=-0.12
VGmax=0.15
VGsub=VG[(VG >= VGmin) & (VG <= VGmax)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

ICsub=np.zeros(Nsub)
VT0sub=np.zeros(Nsub)

for k in range(0,Nsub):
    ICsub[k]=ID[Nmin+k]/Ispec0
    VT0sub[k]=VGsub[k]-nUT*ln(ICsub[k])

VT0wi=np.mean(VT0sub)
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))

plt.plot(VGsub,VT0sub,'r-o', markersize=msize, markevery=1)
plt.plot([VGmin,VGmax],[VT0wi,VT0wi], 'k--')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$V_{T0ext}$ [V]')
plt.ylim(0,0.4)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate('$V_{{T0}} =$' + f'{VT0wi:.3f}', size=9,
             xy=(VGmin, VT0wi), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0wi/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(1.03, 0.5, textstr, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_average')
plt.show()

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The threshold voltage for this wide and long device is surprisingly small. It is in accordance with the documentation giving a typical-typical $V_{TH} \cong 200\,mV$ for $W=10\,\mu m$ and $L=10\,\mu m$.

We can now plot the $I_D$-$V_G$ for this threshold voltage.

In [69]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
lambdac=0
VT0=VT0wi
display(Latex(f'$n  =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps(vps[k])
    idsim[k]=ID[k]/Ispec

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)
    
axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.4)
axs[0].set_xticks(np.arange(-0.4,1.6,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-4,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.4)
axs[1].set_xticks(np.arange(-0.4,1.6,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We get a reasonable fit with some deviations in the moderate inversion, which is expected since we fitted with the asymptotes.

#### Summary

In [70]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
#ax1.set_ylim(1e-4,1e3)
ax1.set_yticks([1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e2)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.2)
#ax3.set_xticks(np.arange(-0.4,1.8,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,350)
ax3.set_yticks(np.arange(0,350,50))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_direct_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

In [71]:
#| label: tbl-medium_sekv_parameters1
#| tbl-cap: Direct extraction of the sEKV parameters for the medium-channel transistor with $\lambda_c=0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"direct with lambdac=0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={3: "medium"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.272e+00 8.500e-07 1.733e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 6.500e-07 2.431e-01   

         lambdac      Lsat                      Comment  
long   0.000e+00 0.000e+00        direct with lambdac=0  
long   0.000e+00 0.000e+00  optimization with lambdac=0  
long   5.500e-02 5.468e-07  optimization with lambdac>0  
medium 0.000e+00 0.000e+00        direct with lambdac=0

### Extraction using optimization with $\lambda_c=0$

#### Slope factor $n$ and $I_{spec}$ extraction

We can try to extract $n$ and $I_{spec}$ for a long-channel directly from the normalized $G_m/I_d$ function.

In [72]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit1(ID,n,Ispec):
    IC=ID/Ispec
    gmsid=gmsid_ic(IC)
    nUT=n*UT
    return gmsid/nUT

Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

nini=n0
Ispecini=Ispec0
    
pars, cov = curve_fit(f=GmIDfit1, xdata=ID, ydata=GmIDsim, p0=[nini,Ispecini], )
n1=pars[0]
Ispec1=pars[1]
Ispecsq1=Ispec1/(Weff/Leff)

n=n1
Ispecsq=Ispecsq1
Ispec=Ispec1
nUT=n*UT
lambdac=0
Lsat=0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,sqrt(1e-3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We get a reasonable fit and values that similar to the direct extraction.

We can also try to keep the value of $n$ extracted from the direct extraction above and optimize for $I_{spec}$ only.

In [73]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit2(ID,Ispec):
    IC=ID/Ispec
    gmsid=gmsid_ic(IC)
    return gmsid/nUT

n=n0
nUT=n*UT
Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

Ispecini=Ispec0
pars, cov = curve_fit(f=GmIDfit2, xdata=ID, ydata=GmIDsim, p0=Ispecini)
Ispec2=pars[0]
Ispecsq2=Ispec2/(Weff/Leff)
lambdac=0

Ispecsq=Ispecsq2
Ispec=Ispec2
lambdac=0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,sqrt(1e-3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is good in weak and moderate inversion, but we still have some discrepancies in strong inversion which is due to mobility reduction due to the vertical field.
We will keep the last extracted values for $I_{specsq}$.

In [74]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

#### Threshold voltage extraction

In [75]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def logIDVGfit(VG,VT0):
    vps=(VG-VT0)/nUT
    IC=ic_vps(vps)
    return ln(IC)

idsim=np.zeros(Npts)
logidsim=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    logidsim[k]=ln(idsim[k])

nUT=n*UT
VT0ini=0.4

pars, cov = curve_fit(f=logIDVGfit, xdata=VG, ydata=logidsim, p0=VT0ini)
VT04=pars[0]

VT0=VT04

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)

VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)

axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.4)
axs[0].set_xticks(np.arange(-0.4,1.6,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-4,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.4)
axs[1].set_xticks(np.arange(-0.4,1.6,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

#saveFigures(savePath, 'ext_param_vs_length')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We see a reasonable fit except in strong inversion. This is expected since we optimized the moderate inversion region.

#### Summary

In [76]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
ax1.set_ylim(1e-4,1e3)
ax1.set_yticks([1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e2)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.4)
ax3.set_xticks(np.arange(-0.4,1.6,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,500)
ax3.set_yticks(np.arange(0,500,100))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_opt_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

The extraction using curve-fitting gives a better fit in moderate inversion but less in strong inversion.

In [77]:
#| label: tbl-medium_sekv_parameters2
#| tbl-cap: Extraction of the sEKV parameters by optimization for the medium-channel transistor with $\lambda_c=0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"optimization with lambdac=0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={4: "medium"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.272e+00 8.500e-07 1.733e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 6.500e-07 2.431e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 7.083e-07 2.456e-01   

         lambdac      Lsat                      Comment  
long   0.000e+00 0.000e+00        direct with lambdac=0  
long   0.000e+00 0.000e+00  optimization with lambdac=0  
long   5.500e-02 5.468e-07  optimization with lambdac>0  
medium 0.000e+00 0.000e+00        direct with lambdac=0  
medium 0.000e+00 0.000e+00  optimization with lambdac=0

### Extraction using optimization with $\lambda_c > 0$

We start extracting $n$, $I_{spec}$ and $\lambda_c$ using curve fitting on $G_m/I_D$.

In [78]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit4(ID,n,Ispec,lambdac):
    nUT=n*UT
    IC=ID/Ispec
    gmsid=gmsid_ic_short(IC,lambdac)
    return gmsid/nUT

Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

nini=n0
Ispecini=Ispec0
lambdacini=0.1

pars, cov = curve_fit(f=GmIDfit4, xdata=ID, ydata=GmIDsim, p0=[nini,Ispecini,lambdacini], )
n4=pars[0]
Ispec4=pars[1]
lambdac4=pars[2]
Ispecsq4=Ispec4*L/W

n=n4
Ispecsq=Ispecsq4
Ispec=Ispec4
lambdac=lambdac4
Lsat=lambdac*Leff

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, 'CS_OL_ib_vs_IC_GBW_Adc_no_VS')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We now have a good fit in strong inversion that we can still improve by slightly reducing the value of $I_{specsq}$, which seems too high and $\lambda_c$.

In [79]:
n=n4
Ispecsq=800e-9
Ispec=Ispecsq*Weff/Leff
lambdac=0.08

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We now have an almost perfect fit.

#### Summary

We can now check the large and small-signal characteristics.

In [80]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.0f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
ax1.set_ylim(1e-4,1e3)
ax1.set_yticks([1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e2)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=4)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.4)
ax3.set_xticks(np.arange(-0.4,1.6,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,)
#ax3.set_yticks(np.arange(0,500,100))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_with_lambdac_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

In [81]:
#| label: tbl-medium_sekv_parameters3
#| tbl-cap: Extraction of the sEKV parameters by optimization for the medium-channel transistor with $\lambda_c>0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"optimization with lambdac>0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={5: "medium"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.272e+00 8.500e-07 1.733e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 6.500e-07 2.431e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 7.083e-07 2.456e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.266e+00 8.000e-07 2.456e-01   

         lambdac      Lsat                      Comment  
long   0.000e+00 0.000e+00        direct with lambdac=0  
long   0.000e+00 0.000e+00  optimization with lambdac=0  
long   5.500e-02 5.468e-07  optimization with lambdac>0  
medium 0.000e+00 0.000e+00        direct with lambdac=0  
medium 0.000e+00 0.000e+00  optimization with lambdac=0  
medium 8.000e-02 8.089e-08  optimization with lambdac>0

## Output characteristic

### Generating the data

In [82]:
simulationPath="./Simulations/" + type + "/idgdsvd/"
dataPath="./Data/" + type + "/"
fileName = "idgdsvd"
dataFile = dataPath + fileName + "_" + type + "_medium.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

VS=0
VD=1.2

#n=1.21
#VT0=173e-3
#Ispecsq=825e-9
idx=4
n=sekv_idvg_param_df.iloc[idx]['n']
Ispecsq=sekv_idvg_param_df.iloc[idx]['Ispecsq']
VT0=sekv_idvg_param_df.iloc[idx]['VT0']
IC=1
Ispec=Ispecsq*Weff/Leff
ID=Ispec*IC
vps=vps_ic(IC)
nUT=n*UT
VG=VT0+nUT*vps

Npts=201
VDmin=0
VDmax=1.2
dVD=(VDmax-VDmin)/(Npts-1)

if newSim:
    paramstr = '\n'.join((
        f'.param W={W/1e-6:.2f}u L={L/1e-6:.2f}u VG={VG:.1f} VS={VS:.1f} VD={VD:.1f}',
        f'.csparam VDmin = {VDmin:.3f}',
        f'.csparam VDmax = {VDmax:.3f}',
        f'.csparam dVD = {dVD:.3f}'
    ))
    #print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationPath + fileName + ".log", 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

### Importing and plotting the data

#### I~D~ and G~ds~ versus V~D~

In [83]:
df_idgdsvd=pd.read_table(dataFile, sep=' +', engine='python')
VD=df_idgdsvd['v-sweep'].to_numpy()
ID=df_idgdsvd['ID'].to_numpy()
Gds=df_idgdsvd['Gds'].to_numpy()

Type='nMOS (t-t)'

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].plot(VD, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
mosinfo = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$',
    f'$V_S =$ {VS:.0f} V',
    f'$IC \\cong$ {IC:.0f}',
    f'$V_G =$ {VG/1e-3:.0f} mV'))
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VD, abs(Gds)/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [84]:
def diff(y, dx):
    N=len(y)
    dydx=np.zeros(N)
    dydx[0]=(y[1]-y[0])/dx
    dydx[1]=(y[2]-y[0])/(2*dx)
    for k in range(2,N-2):
        dydx[k]=(y[k-2]-8*y[k-1]+8*y[k+1]-y[k+2])/(12*dx)
    dydx[N-2]=(y[N-1]-y[N-3])/(2*dx)
    dydx[N-1]=(y[N-1]-y[N-2])/dx
    return dydx

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]
Gdsnum=np.zeros(Npts)
dVD=VD[1]-VD[0]
Gdsnum=diff(ID,dVD)

plt.semilogy(VD, Gds/1e-6,'ro', label='Data', markersize=msize, markevery=mevery)
plt.semilogy(VD, Gdsnum/1e-6,'b-', label='Num. diff.')
plt.xlabel('$V_D$ [V]')
plt.xlim(VDmin,VDmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_{ds}$ [$\\mu A/V$]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower left')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

The output conductance calculated by differentiating the large-signal $I_D$-$V_D$ matches the value extracted from the PSP model. We will keep the value from PSP.

#### Filtering the outliers

In [85]:
VDmini=0.15
VDmaxi=1.2

VDsub=VD[(VD >= VDmini) & (VD <= VDmaxi)]
Nsub=len(VDsub)
Nmin=np.where(VD == VDsub[0])[0][0]
Nmax=np.where(VD == VDsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
Gdssub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    Gdssub[k]=Gds[Nmin+k]

Nfil=Npts-Nsub
VDfil=np.zeros(Nfil)
IDfil=np.zeros(Nfil)
Gdsfil=np.zeros(Nfil)

for k in range(0,Nfil):
    VDfil[k]=VD[k]
    IDfil[k]=ID[k]
    Gdsfil[k]=Gds[k]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)

axs[0].plot(VDfil, IDfil/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[0].plot(VDsub, IDsub/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VDfil, abs(Gdsfil)/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[1].semilogy(VDsub, abs(Gdssub)/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

### Extracting the CLM parameter

In [86]:
from scipy.stats import linregress

slope, intercept, _, _, _ = linregress(VDsub, IDsub)
Gdsext=slope
ID0ext=intercept
VEext=-ID0ext/Gdsext
lambdaext=-VEext/L

display(Latex(f'$G_{{ds}} =$ {Gdsext/1e-6:.3f} $\\mu A/V$'))
display(Latex(f'$I_{{D0}} =$ {ID0ext/1e-6:.3f} $\\mu A$'))
display(Latex(f'$V_E =$ {VEext:.3f} $V$'))
display(Latex(f'$\\lambda =$ {lambdaext/1e6:.3f} $V/\\mu m$'))

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]

IDfit=np.zeros(Npts)
Gdsfit=np.zeros(Npts)

for k in range(0,Npts):
#    IDfit[k]=ID0ext+Gdsext*VD[k]
    IDfit[k]=Gdsext*(VD[k]-VEext)
    Gdsfit[k]=Gdsext

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)

axs[0].plot(VDfil, IDfil/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[0].plot(VDsub, IDsub/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[0].plot(VD, IDfit/1e-6, 'k--', label='Fit')
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,1.6,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
#axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
textstr1 = '\n'.join((
    f'$I_{{D0}} =$ {ID0ext/1e-6:.3f} $\\mu A$',
    f'$G_{{ds}} =$ {Gdsext/1e-6:.3f} $\\mu A/V$',
    f'$V_E =$ {VEext:.3f} V',
    f'$\\lambda =$ {lambdaext/1e6:.3f} $V/\\mu m$'))
axs[0].text(0.6, 0.05, textstr1, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VDfil, abs(Gdsfil)/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[1].semilogy(VDsub, abs(Gdssub)/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[1].semilogy(VD, Gdsfit/1e-6, 'k--', label='Fit')
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2400x900 with 2 Axes>

We get a rather high output conductance and hence low value of the $\lambda$ parameter for such a long transistor.

In [87]:
#| label: tbl-medium_clm_parameters1
#| tbl-cap: CLM parameters extracted for the medium-channel transistor in moderate inversion.

sekv_idvd_param_df.loc[len(sekv_idvd_param_df.index)] = [W,Weff,L,Leff,IC,Gdsext,ID0ext,VEext,lambdaext,"moderate"]
sekv_idvd_param_df = sekv_idvd_param_df.rename(index={1: "medium"})
sekv_idvd_param_df

W      Weff         L      Leff  IC       Gds       ID0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06   1 2.105e-07 6.119e-07   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07   1 5.124e-07 7.048e-07   

               VE    lambda   Comment  
long   -2.907e+00 2.907e+05  moderate  
medium -1.375e+00 1.375e+06  moderate

## Noise

In this section we will extract the flicker noise parameters to be used with sEKV and check the white noise power spectral desnity (PSD). We reuse the flicker noise model from EKV 2.6, where the input (gate) referred PSD is given by

\begin{equation}
  S_{nin,fl}(f) = \frac{KF}{W_{eff}\,L_{eff}\,C_{ox}\; f^{AF}}
\end{equation}

In this model the flicker noise is assumed to scale as $1/C_{ox}$, which is correct if the noise follows the the Hooge model (i.e. originates from mobility fluctuations). In the case of the Mc Worther model (i.e. flicker noise originating from traps in Si-SiO~2~ interface and in the oxyde), the PSD scales as $C_{ox}^2$. Despiet the flicker noise is usually domanted by the trapping mechanism, we will keep the above model with a $1/C_{ox}$ scaling.

In EKV , we like to rewrite the flicker noise PSD like the thermal noise in terms of a input-referred noise resistance

\begin{equation}
  S_{nin,fl}(f) = 4 kT\,R_{nin,fl}(f)
\end{equation}

where

\begin{equation}
  R_{nin,fl}(f) = \frac{\rho}{W_{eff}\,L_{eff}\,f^{AF}}
\end{equation}

with

\begin{equation}
  \rho = \frac{KF}{4 kT\,C_{ox}}
\end{equation}

Note that the flicker noise parameter have some weird units. Indeed, $KF$ is in $A \cdot V \cdot s^{2-AF}$ and $\rho$ is in $V \cdot m^2 / (A \cdot s^{AF})$. If $AF = 1$, like it is often the case, then $KF$ is in $A \cdot V \cdot s$ and $\rho$ is in $V \cdot m^2 / (A \cdot s)$.

To extract the noise parameters, we use a common-source stage loaded by a noiseless resistor. We first will set the bias condition in terms of $IC$ and calculate the input-referred white noise to compare it to the result obtained from the PSP simulations.

### Setting bias conditions

Having extracted $n$, $I_{spec\Box}$ and $V_{T0}$, we can impose the inversion coefficient and calculate the corresponding gate voltage $V_G$. We nee to make sure the transistor remains in saturation.

In [88]:
#n=1.21
#VT0=173e-3
#Ispecsq=825e-9
tox=2.2404e-09
Cox=epsilonox*epsilon0/tox
idx=4
n=sekv_idvg_param_df.iloc[idx]['n']
Ispecsq=sekv_idvg_param_df.iloc[idx]['Ispecsq']
VT0=sekv_idvg_param_df.iloc[idx]['VT0']

VDD=1.5
IC=1
Ispec=Ispecsq*Weff/Leff
ID=Ispec*IC
#qs=q_ic(IC)
vps=vps_ic(IC)
nUT=n*UT
VG=VT0+nUT*vps
VS=0
gms=gms_ic(IC)
Gmekv=Ispec/nUT*gms
gammanekv=gamman_ic(IC,n)
Rnthekv=gammanekv/Gmekv
Snthekv=4*kT*Rnthekv
Vnthekv0=sqrt(Snthekv)
Av=10
RL=Av/Gmekv
VRL=ID*RL
VDS=VDD-VRL
VDSsat=UT*vdssat_ic(IC)
region="saturation" if VDS > VDSsat else "linear"

display(Latex(f'$W =$ {W/1e-6:.0f} $\\mu m$'))
display(Latex(f'$L =$ {L/1e-6:.0f} $\\mu m$'))
display(Latex(f'$IC =$ {IC:.0f}'))
display(Latex(f'$I_{{D}} =$ {ID/1e-6:.3f} $\\mu A$'))
display(Latex(f'$V_{{G}} =$ {VG:.3f} $V$'))
display(Latex(f'$V_{{S}} =$ {VS:.3f} $V$'))
display(Latex(f'$G_{{m}} =$ {Gmekv/1e-6:.3f} $\\mu A/V$'))
display(Latex(f'$\\gamma_n =$ {gammanekv:.3f}'))
display(Latex(f'$R_{{n,th}} =$ {Rnthekv/1e3:.3f} $k \\Omega$'))
display(Latex(f'$S_{{n,th}} =$ {Snthekv:.3e} $V^2/Hz$'))
display(Latex(f'$V_{{n,th}} =$ {Vnthekv0/1e-9:.3f} $nV/\\sqrt{{Hz}}$'))
display(Latex(f'$A_v =$ {Av:.0f}'))
display(Latex(f'$R_L =$ {RL/1e3:.3f} $k \\Omega$'))
display(Latex(f'$V_{{DD}} =$ {VDD:.3f} $V$'))
display(Latex(f'$V_{{RL}} =$ {VRL:.3f} $V$'))
display(Latex(f'$V_{{DS}} =$ {VDS:.3f} $V$'))
display(Latex(f'$V_{{DSsat}} =$ {VDSsat:.3f} $V$'))
print(f'The transistor is biased in the {region} region')

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

...

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

The transistor is biased in the saturation region


### Extract operating point information

In [89]:
simulationPath="./Simulations/" + type + "/noise/"
dataPath="./Data/" + type + "/"
fileName = "noise"
dataFile = dataPath + fileName + "_" + type + "_medium.op.dat"
opFile = simulationPath + fileName + ".op.dat"
paramFile = simulationPath + fileName + ".op.par"
simulationFile = simulationPath + fileName + ".op.cir"
simulationLog = simulationPath + fileName + ".op.log"
simulationData = simulationPath + fileName + ".op.dat"

if newSim:
    paramstr = '\n'.join((
        f'.param VDD={VDD:.1f} VG={VG:.3f} RL={RL/1e3:.3f}k',
        f'.param W={W/1e-6:.0f}u L={L/1e-6:.0f}u'
    ))
    print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationLog, 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

We can extract the values of the PSP noise parameters from the operating point informations.

In [90]:
mosop_df=pd.read_table(dataFile, sep=r'\s+', dtype=np.float64, engine='python')
mosop_df=mosop_df.rename(columns={'@n.xn.nsg13_lv_nmos[weff]': 'Transistor',
                              '@n.xn.Nsg13_lv_nmos[weff]': 'Weff',
                              '@n.xn.Nsg13_lv_nmos[leff]': 'Leff',
                              '@n.xn.Nsg13_lv_nmos[ids]': 'IDS',
                              '@n.xn.Nsg13_lv_nmos[gm]': 'Gm',
                              '@n.xn.Nsg13_lv_nmos[gds]': 'Gds',
                              '@n.xn.Nsg13_lv_nmos[sid]': 'Snidth',
                              '@n.xn.Nsg13_lv_nmos[sqrtsfw]': 'Vninth',
                              '@n.xn.Nsg13_lv_nmos[sfl]': 'Snidfl @ 1Hz',
                              '@n.xn.Nsg13_lv_nmos[sqrtsff]': 'Vninfl @ 1kHz',
                              '@n.xn.Nsg13_lv_nmos[fknee]': 'fk'
                    })
mosop_df['Transistor'] = mosop_df['Transistor'].astype(str)
mosop_df.at[0, 'Transistor'] = 'Mn'
mosop_df.set_index('Transistor', inplace=True)
mosop_df.rename_axis(index=None, inplace=True)

Weffpsp=mosop_df.at['Mn','Weff']
Leffpsp=mosop_df.at['Mn','Leff']
Gmpsp=mosop_df.at['Mn','Gm']
Snidthpsp=mosop_df.at['Mn','Snidth']
Snidfl1Hzpsp=mosop_df.at['Mn','Snidfl @ 1Hz']
Snthpsp=Snidthpsp/Gmpsp**2
Vnthpsp0=mosop_df.at['Mn','Vninth']
Snfl1Hzpsp=Snidfl1Hzpsp/Gmpsp**2
Vnfl1Hzpsp=sqrt(Snfl1Hzpsp)
Vnfl1kHzpsp=mosop_df.at['Mn','Vninfl @ 1kHz']
KFpsp=Snfl1Hzpsp*Weffpsp*Leffpsp*Cox # Definition from EKV 2.6
KFlong=KFpsp
rhopsp=KFpsp/(4*kT*Cox)
rholong=rhopsp
AFpsp=log(Snfl1Hzpsp/Vnfl1kHzpsp**2)/3
fkpsp=mosop_df.at['Mn','fk']
Rnthpsp=Snthpsp/(4*kT)
gammanpsp=Gmpsp*Rnthpsp

display(Latex(f'$V_{{n,th}} =$ {Vnthpsp0/1e-9:.3f} $nV/\\sqrt{{Hz}}$ (PSP)'))
display(Latex(f'$f_k=$ {fkpsp/1e3:.3f} $kHz$ (PSP)'))
display(Latex(f'$KF =$ {KFpsp:.3e} $V A s$ (PSP)'))
display(Latex(f'$\\rho =$ {rhopsp:.3f} $V m^2/(A s)$ (PSP)'))
display(Latex(f'$AF =$ {AFpsp:.3f} (PSP)'))
display(Latex(f'$R_{{n,th}} =$ {Rnthpsp/1e3:.3f} $k \\Omega$ (PSP)'))
display(Latex(f'$\\gamma_n =$ {gammanpsp:.3f} (PSP)'))

mosop_df

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Weff      Leff       IDS        Gm       Gds    Snidth    Vninth  \
Mn 1.020e-06 9.412e-07 6.936e-07 1.402e-05 2.666e-07 1.745e-25 2.979e-08   

    Snidfl @ 1Hz  Vninfl @ 1kHz        fk  
Mn     2.934e-20      3.863e-07 1.681e+05

### Simulating noise PSD

We can now simulate the PSD and check against the EKV model.

In [91]:
simulationPath="./Simulations/" + type + "/noise/"
dataPath="./Data/" + type + "/"
fileName = "noise"
dataFile = dataPath + fileName + "_" + type + "_medium.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"


fmin=1
fmax=1e8
decPts=21

if newSim:
    paramstr = '\n'.join((
        f'.param VDD={VDD:.1f} VG={VG:.3f} RL={RL/1e3:.0f}k',
        f'.param W={W/1e-6:.0f}u L={L/1e-6:.0f}u',
        f'.csparam fmin = {fmin:.0e}',
        f'.csparam fmax = {fmax:.0e}',
        f'.csparam decPts = {decPts:.0f}'
    ))
    print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationLog, 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

In [92]:
df_noise=pd.read_table(dataFile, sep=' +', engine='python')
freq=df_noise['frequency'].to_numpy()
Vninpsp=df_noise['inoise_spectrum'].to_numpy()
Vnoutpsp=df_noise['onoise_spectrum'].to_numpy()

Type='nMOS (t-t)'

Npts=len(freq)
fmin=freq[0]
fmax=freq[Npts-1]

Vnthekv=np.zeros(Npts)
Snflekv=np.zeros(Npts)
Vnflekv=np.zeros(Npts)

for k in range(0,Npts):
    Vnthekv[k]=Vnthekv0
    Snflekv[k]=KFpsp/(Weff*Leff*Cox*freq[k])
    Vnflekv[k]=sqrt(Snflekv[k])

plt.loglog(freq, Vnoutpsp,'r-', label='Output noise (PSP)')
plt.loglog(freq, Vninpsp,'b-', label='Input noise (PSP)')
plt.loglog(freq, Vnthekv,'k--', label='White input noise (sEKV)')
plt.loglog(freq, Vnflekv,'k-.', label='Flicker input noise (model)')
#plt.loglog([fk,fk],[1e-10,Vnth],'k--')
plt.xlim(fmin,fmax)
#plt.xticks([1e0,1e1,1e2,1e3,1e4,1e5,1e6,1e7,1e8,1e9])
plt.xlabel('Frequency [Hz]')
plt.ylim(1e-9,1e-5)
plt.ylabel('$\\sqrt{S_{nout}}$ and $\\sqrt{S_{nin}}$ $[V/\\sqrt{Hz}]$')
plt.legend(loc='lower left', fontsize=9)
#plt.legend(loc='center left', fontsize=9, bbox_to_anchor=(1, 0.5))
textstr1 = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$'))
textstr2 = '\n'.join((
    f'$IC =$ {IC:.0f}',
    f'$V_G =$ {VG:.3f} V',
    f'$V_{{DS}} =$ {VDS:.3f} V',
    f'$R_L =$ {RL/1e3:.1f} $k\\Omega$'))
textstr3 = '\n'.join((
    f'$G_m =$ {Gmpsp/1e-6:.3f} $\\mu A/V$ (PSP)',
    f'$G_m =$ {Gmekv/1e-6:.3f} $\\mu A/V$ (EKV)',
    f'$\\sqrt{{S_{{in,th}}}} =$ {Vnthpsp0:.3e} (PSP)',
    f'$\\sqrt{{S_{{in,th}}}} =$ {Vnthekv0:.3e} (EKV)',
#    f'$R_{{n,th}} =$ {Rnthpsp/1e3:.3f} $k\\Omega$ (PSP)',
#    f'$R_{{n,th}} =$ {Rnthekv/1e3:.3f} $k\\Omega$ (EKV)',
    f'$\\gamma_n =$ {gammanpsp:.3f} (PSP)',
    f'$\\gamma_n =$ {gammanekv:.3f} (EKV)',
    f'$KF =$ {KFpsp:.3e} $V A s$ (PSP)',
    f'$\\rho =$ {rhopsp:.3e} $V m^2/(A s)$ (PSP)',
    f'$AF =$ {AFpsp:.3f} (PSP)',
    f'$f_k =$ {fkpsp/1e3:.3f} kHz (PSP)'))
plt.text(0.4, 0.95, textstr1, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.text(0.7, 0.95, textstr2, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.text(1.05, 0.5, textstr3, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#plt.text(fk, 1e-9, '$f_k =$'+f'{fk/1e3:.0f} kHz', ha='left', va='bottom', size=14)
#plt.text(1e2, Vnth, '$\sqrt{S_{nin,th}} =$'+f'{Vnth/1e-9:.1f} '+'$nV/\sqrt{Hz}$', ha='center', va='bottom', size=14)
#saveFigures(savePath, 'Input_referred_noise_PSD')
plt.show()

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 1200x900 with 1 Axes>

The flicker noise parameters are given by

In [93]:
#| label: tbl-medium_noise_parameters
#| tbl-cap: Extraction of the noise parameters for the medium-channel transistor.

KFn=KFpsp
rhon=rhopsp
AFn=AFpsp

sekv_noise_param_df.loc[len(sekv_noise_param_df.index)] = [W,Weff,L,Leff,IC,KFn,AFn,rhon,"moderate"]
sekv_noise_param_df = sekv_noise_param_df.rename(index={1: "medium"})
sekv_noise_param_df

W      Weff         L      Leff  IC        KF        AF  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06   1 3.175e-24 1.000e+00   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07   1 2.208e-24 1.000e+00   

             rho   Comment  
long   1.243e-02  moderate  
medium 8.642e-03  moderate

# Short-channel parameters

## DC Transfer Characteristic Parameters

### Generating the data

In [94]:
simulationPath="./Simulations/" + type + "/idgmvg/"
dataPath="./Data/" + type + "/"
fileName = "idgmvg"
dataFile = dataPath + fileName + "_" + type + "_short.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

W=10e-6
L=130e-9
Weff=effectiveW(W,L)
Leff=effectiveL(W,L)
VG=1
VS=0
VD=1.5

Npts=201
VGmin=-0.5
VGmax=1.5
dVG=(VGmax-VGmin)/(Npts-1)

if newSim:
    paramstr = '\n'.join((
        f'.param W={W/1e-6:.2f}u L={L/1e-6:.2f}u VG={VG:.1f} VS={VS:.1f} VD={VD:.1f}',
        f'.csparam VGmin = {VGmin:.3f}',
        f'.csparam VGmax = {VGmax:.3f}',
        f'.csparam dVG = {dVG:.3f}'
    ))
    #print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationPath + fileName + ".log", 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

### Importing and plotting the data

#### I~D~ and G~m~ versus V~G~

In [95]:
df_idgmvg=pd.read_table(dataFile, sep=' +', engine='python')
VG=df_idgmvg['v-sweep'].to_numpy()
ID=df_idgmvg['ID'].to_numpy()
Gm=df_idgmvg['Gm'].to_numpy()

Type='nMOS (t-t)'

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
mosinfo = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-9:.0f} $nm$',
    f'$V_S =$ {VS:.0f} V',
    f'$V_D =$ {VD:.1f} V'))
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VG, abs(Gm)/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_m|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [96]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
axs[0].text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$I_D$ [$\\mu A$]')
axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [97]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].semilogy(VG, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_G$ [V]')
axs[0].set_xlim(VGmin,VGmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
#axs[0].set_ylim(1e-4,1e3)
#axs[0].legend(loc='upper left')
axs[0].text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VG, sqrt(ID)/1e-3, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_G$ [V]')
axs[1].set_xlim(VGmin,VGmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$\\sqrt{{I_D}}$ [$\\sqrt{{\\mu A}}$]')
axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 2400x900 with 2 Axes>

#### G~m~-V~G~

In [98]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
Gmnum=np.zeros(Npts)
dVG=VG[1]-VG[0]
Gmnum=diff(ID,dVG)

plt.semilogy(VG, abs(Gm)/1e-6,'ro', label='Data', markersize=msize, markevery=mevery)
plt.semilogy(VG, abs(Gmnum)/1e-6,'b-', label='Num. diff.')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_m$ [$\\mu A/V$]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

We see that the transconductance obtained by differentiating the large-signal $I_D$-$V_G$ characteristic is equal to the transconductance extracted from the PSP model. We will keep the value extracted from the PSP model.

#### G~m~-I~D~

In [99]:
Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

plt.loglog(ID, Gm,'ro', label='Data', markersize=msize, markevery=mevery)
plt.loglog(ID, Gmnum,'b-', label='Num. diff.')
plt.xlabel('$I_D$ [A]')
#plt.xlim(1e-12,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
textstr = '\n'.join((
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-6:.0f} $\\mu m$'))
plt.text(0.05, 0.95, mosinfo, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

#### Filtering the outliers

In [100]:
VGmini=0
VGmaxi=1.5

VGsub=VG[(VG >= VGmini) & (VG <= VGmaxi)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
Gmsub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    Gmsub[k]=Gm[Nmin+k]

Nfil=Npts-Nsub
VGfil=np.zeros(Nfil)
IDfil=np.zeros(Nfil)
Gmfil=np.zeros(Nfil)

for k in range(0,Nfil):
    VGfil[k]=VG[k]
    IDfil[k]=ID[k]
    Gmfil[k]=Gm[k]

plt.semilogy(VGfil, IDfil, 'b-o', label='Outliers', markersize=msize, markevery=4)
plt.semilogy(VGsub ,IDsub, 'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$I_D$ [A]')
#plt.ylim(1e-12,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_ID_VG_outliers')
plt.show()

<Figure size 1200x900 with 1 Axes>

In [101]:
plt.semilogy(VGfil,abs(Gmfil),'b-o', label='Outliers', markersize=msize, markevery=2)
plt.semilogy(VGsub,abs(Gmsub),'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin, VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-10,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_Gm_VG_outliers')
plt.show()

<Figure size 1200x900 with 1 Axes>

In [102]:
plt.loglog(IDfil,Gmfil,'b-o', label='Outliers', markersize=msize, markevery=2)
plt.loglog(IDsub,Gmsub,'r-o', label='Selected', markersize=msize, markevery=4)
plt.xlabel('$I_D$ [A]')
#plt.xlim(1e-10,1e-3)
#plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.ylabel('$G_m$ [A/V]')
#plt.ylim(1e-9,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower right')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

In [103]:
VG=VGsub
ID=IDsub
Gm=Gmsub

## Direct extraction with $\lambda_c=0$

### Slope factor $n$ and $I_{spec}$ extraction

The gate transconductance in weak inversion and saturation is given by
\begin{equation}
  G_m = \frac{I_D}{n\,U_T}.
\end{equation}
So if we plot $I_D/(G_m\,U_T)$ we should see a plateau in weak inversion the value of which is equal to the slope factor $n$.

In [104]:
Npts=len(VG)
next=np.zeros(Npts)

for k in range(0,Npts):
    next[k]=ID[k]/(Gm[k]*UT)

nextmin=np.min(next)
Nmin=np.where(next == nextmin)[0]
IDext=ID[Nmin[0]]
n0=round(nextmin,2)
display(Latex(f'$n =$ {n0:.2f}'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-9:.2f} $nA$'))

plt.loglog(ID,next,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[n0,n0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1,n0],'k--', linewidth=lw)
plt.loglog(ID[Nmin],next[Nmin],'ko', markersize=msize)
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.xlabel('$I_D$ [A]')
plt.ylim(1,1e2)
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$n =$ {n0:.2f}', size=9,
             xy=(1e-10, n0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_D =$ {IDext/1e-9:.0f} nA', size=9,
             xy=(IDext, 1), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='top')
textstr = '\n'.join((
    mosinfo,
    r'$n =$'+ f'{n0:.2f}'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_n_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

In [105]:
Ispecext=np.zeros(Npts)
nUT=n0*UT

for k in range(0,Npts):
    Ispecext[k]=(Gm[k]*nUT)**2/ID[k]

Ispec0=np.max(Ispecext)
Ispecsq0=Ispec0/(Weff/Leff)
Nmax=np.where(Ispecext == Ispec0)[0]
IDext=ID[Nmax[0]]

display(Latex(f'$W_{{eff}} =$ {Weff/1e-6:.3f} $\\mu m$'))
display(Latex(f'$L_{{eff}} =$ {Leff/1e-9:.3f} $nm$'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-3:.3f} $mA$'))

plt.loglog(ID,Ispecext,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[Ispec0,Ispec0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1e-12,Ispec0],'k--', linewidth=lw)
plt.loglog(ID[Nmax],Ispecext[Nmax],'ko', markersize=msize)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.ylabel('$(G_m\\,n\\,U_T)^2/I_D$ [A]')
plt.ylim(1e-10,1e-4)
plt.annotate(f'$I_{{spec}} =$ {Ispec0/1e-6:.1f} $\\mu A$', size=9,
             xy=(1e-10, Ispec0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_D =$ {IDext/1e-3:.2f} $mA$', size=9,
             xy=(IDext, 1e-10), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}',
    f'$I_{{spec}} =$ {Ispec0/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
plt.text(0.5, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_Ispec_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

In [106]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0

display(Latex(f'$n =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))

Next=101
IDsi=np.linspace(Ispec0,1e-2,Next,endpoint=True)
IDGmUTsi=np.zeros(Next)

for k in range(0,Next):
    IDGmUTsi[k]=n*sqrt(IDsi[k]/Ispec)

plt.loglog(ID,next,'r-o', markersize=msize, markevery=2)
plt.loglog(IDsi,IDGmUTsi,'k--', linewidth=lw)
plt.loglog([1e-12,Ispec],[n,n],'k--', linewidth=lw)
plt.loglog([Ispec,Ispec],[1,n],'k--', linewidth=lw)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-2)
plt.xticks([1e-12,1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
plt.ylim(1,1e2)
plt.annotate(f'$n =$ {n:.2f}', size=9,
             xy=(1e-10, n), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$', size=9,
             xy=(Ispec, 1), xycoords='data',
             xytext=(50, 15), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='bottom')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.1f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_n_Ispec')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

Having extracted $n$ and $I_{spec}$, we can now plot the normalized $G_m/I_D$ function.

In [107]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
lambdac=0
Lsat=0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.0f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-0:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e2],[1,1e-1],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_GmID_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is reasonable over the entire $IC$ span. There is a strange bump in the moderate inversion which comes from the simulation data.
There is some discrepancy in the moderate inversion region which is due to the mobility reduction due to the vertical field appearing for $IC >10^2$. The latter can be accounted for by using the $\lambda_c$ parameter which is normally used for modeling the effect of velocity saturation in short-channel transistor but can also be used to correct the effect of mobility reduction due to the vertical field appearing in long-channel transistors. We will not do this here since we want to extract the long-channel parameters keeping $\lambda_c=0$, but since we are mostly interested in the moderate inversion region, we can slightly increase $I_{spec}$ to improve the fit in moderate inversion at the cost of a degradation in strong inversion.

In [108]:
Ispecsq=350e-9
Ispec=Ispecsq*Weff/Leff

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.0f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-0:.0f}'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e2],[1,1e-1],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlabel('$IC$ [-]')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_GmID_direct_modified')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is now much better in moderate inversion but less in strong inversion. This is due to mobility reduction due to the vertical field an effect that is not accounted for in the model. However, we will keep the new values.

### Threshold voltage extraction

We can extract the threshold voltage in weak inversion (assuming $V_S=0$) from the normalized current (inversion coefficient) given by
\begin{equation}
  IC = e^{\frac{V_G-V_{T0}}{n U_T}}.
\end{equation}
We can now plot
\begin{equation}
  V_{T0} = V_G -n U_T \ln(IC)
\end{equation}
to extract the threshold voltage.

In [109]:
# We keep the initial values of n, Ispecsq and Ispec
#n=n0
#Ispecsq=Ispecsq0
#Ispec=Ispec0
# We keep the new values of n, Ispecsq and Ispec
n0=n
Ispecsq0=Ispecsq
Ispec0=Ispec
nUT=n*UT

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.0f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-0:.0f}'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

ICsim=np.zeros(Npts)
VT0ext=np.zeros(Npts)

nUT=n0*UT

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    VT0ext[k]=VG[k]-nUT*ln(ICsim[k])

plt.plot(VG,VT0ext,'r-o', markersize=msize, markevery=mevery)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$V_{T0ext}$ [V]')
#plt.ylim(0,1.8)
#plt.yticks(np.arange(0,1.1,0.1))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(0.05, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We see a plateau in weak inversion where we can average its value to get the threshold voltage in weak inversion.

In [110]:
VGmin=0
VGmax=0.3
VGsub=VG[(VG >= VGmin) & (VG <= VGmax)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

ICsub=np.zeros(Nsub)
VT0sub=np.zeros(Nsub)

for k in range(0,Nsub):
    ICsub[k]=ID[Nmin+k]/Ispec0
    VT0sub[k]=VGsub[k]-nUT*ln(ICsub[k])

VT0wi=np.mean(VT0sub)
display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))

plt.plot(VGsub,VT0sub,'r-o', markersize=msize, markevery=1)
plt.plot([VGmin,VGmax],[VT0wi,VT0wi], 'k--')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$V_{T0ext}$ [V]')
plt.ylim(0,0.8)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate('$V_{{T0}} =$' + f'{VT0wi:.3f}', size=9,
             xy=(VGmin, VT0wi), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.0f} $\\mu A$',
    f'$V_{{T0}} =$ {VT0wi/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
plt.text(1.03, 0.5, textstr, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_long_VT0_average')
plt.show()

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The threshold voltage for this wide and short device is smaller than what is given in the documentation giving a typical-typical $V_{TH} \cong 500\,mV$ for $W=10\,\mu m$ and $L=130\,nm$.

We can now plot the $I_D$-$V_G$ for this threshold voltage.

In [111]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
nUT=n*UT
lambdac=0
Lsat=0
VT0=VT0wi

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-0:.0f}'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps(vps[k])
    idsim[k]=ID[k]/Ispec

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)
    
axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.2)
axs[0].set_xticks(np.arange(-0.4,1.4,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-4,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.2)
axs[1].set_xticks(np.arange(-0.4,1.4,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We get a reasonable fit in weak and moderate inversion. However, there is a strong deviation in strong inversion due to short channel effects (mainly velocity saturation).

### Summary

In [112]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-0:.0f}'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
ax1.set_ylim(1e-5,1e3)
ax1.set_yticks([1e-5,1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2,1e3])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.0f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.0f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
#ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
#ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e1)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
#ax2.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1e2, 1/lambdac), xycoords='data',
#             xytext=(25, 0), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.1)
ax3.set_xticks(np.arange(-0.4,1.2,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,)
#ax3.set_yticks(np.arange(0,350,50))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
#ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
#ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(ICmin,ICmax)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
#ax4.annotate('$1/\lambda_c =$' + f'{1/lambdac:.1f}', size=9,
#             xy=(1/lambdac, 1e-2), xycoords='data',
#             xytext=(0, -25), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.annotate('$1/\lambda_c^2 =$' + f'{1/lambdac**2:.0f}', size=9,
#             xy=(1/lambdac**2, 1e-2), xycoords='data',
#             xytext=(0, -37), textcoords='offset points',
#             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
#             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
#             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_long_direct_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

We see a big discrepancy in moderate and even larger in strong inversion. This explain the discrepancy between model and simulations for short-channel transistors when using the long-channel model with $\lambda_c=0$.

### Direct extraction with $\lambda_c > 0$

#### Slope factor $n$ extraction

The gate transconductance in weak inversion and saturation is given by
\begin{equation}
  G_m = \frac{I_D}{n\,U_T}.
\end{equation}
So if we plot $I_D/(G_m)\,U_T$ we should see a plateau in weak inversion the value of which is equal to the slope factor $n$.

In [113]:
Npts=len(VG)
next=np.zeros(Npts)

for k in range(0,Npts):
    next[k]=ID[k]/(Gm[k]*UT)

nextmin=np.min(next)
Nmin=np.where(next == nextmin)[0]
IDext=ID[Nmin[0]]
n0=round(nextmin,2)

display(Latex(f'$n =$ {n0:.2f}'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-9:.2f} $nA$'))

plt.loglog(ID,next,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[n0,n0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1,n0],'k--', linewidth=lw)
plt.loglog(ID[Nmin],next[Nmin],'ko', markersize=5)
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.xlabel('$I_D$ [A]')
plt.ylim(1,1e2)
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$n =$ {n0:.2f}', size=9,
             xy=(1e-10, n0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_D =$ {IDext/1e-9:.0f} nA', size=9,
             xy=(IDext, n0), xycoords='data',
             xytext=(0, 30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='bottom')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_short_n_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

#### Specific current $I_{spec}$ extraction

On the other hand the normalized $G_m/I_D$ function for a long-channel transistor in strong inversion and saturation is given by
\begin{equation}
  \frac{G_m\,n\,U_T}{I_D} = \frac{1}{\sqrt{IC}} = \sqrt{\frac{I_{spec}}{I_D}}.
\end{equation}
We can then plot $(G_m\,n\,U_T)^2/I_D$ which should find a maximum value equal to $I_{spec}$.

In [114]:
Ispecext=np.zeros(Npts)
nUT=n0*UT

for k in range(0,Npts):
    Ispecext[k]=(Gm[k]*nUT)**2/ID[k]

Ispec0=np.max(Ispecext)
Ispecsq0=Ispec0/(Weff/Leff)
Nmax=np.where(Ispecext == Ispec0)[0]
IDext=ID[Nmax[0]]

display(Latex(f'$n =$ {n0:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec0/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq0/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-3:.3f} $mA$'))

plt.loglog(ID,Ispecext,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-12,IDext],[Ispec0,Ispec0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1e-12,Ispec0],'k--', linewidth=lw)
plt.loglog(ID[Nmax],Ispecext[Nmax],'ko', markersize=5)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.ylabel('$(G_m\\,n\\,U_T)^2/I_D$ [A]')
plt.ylim(1e-10,1e-4)
plt.annotate(f'$I_{{spec}} =$ {Ispec0/1e-6:.0f} $\\mu A$', size=9,
             xy=(1e-10, Ispec0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_D =$ {IDext/1e-3:.2f} $mA$', size=9,
             xy=(IDext, 1e-10), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n0:.2f}',
    f'$I_{{spec}} =$ {Ispec0/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq0/1e-9:.0f} nA'))
plt.text(0.5, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_short_Ispec_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

In [115]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.0f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))

Next=101
IDsi=np.linspace(Ispec0,1e-2,Next,endpoint=True)
IDGmUTsi=np.zeros(Next)

for k in range(0,Next):
    IDGmUTsi[k]=n*sqrt(IDsi[k]/Ispec)

plt.loglog(ID,next,'r-o', markersize=5, markevery=4)
plt.loglog(IDsi,IDGmUTsi,'k--', linewidth=lw)
plt.loglog([1e-10,Ispec],[n,n],'k--', linewidth=lw)
plt.loglog([Ispec,Ispec],[1,n],'k--', linewidth=lw)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
plt.ylim(1,1e2)
plt.annotate(f'$n =$ {n:.2f}', size=9,
             xy=(1e-10, n), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$', size=9,
             xy=(Ispec, 1), xycoords='data',
             xytext=(15, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

#### Velocity saturation parameter $\lambda_c$ extraction

We can extract $\lambda_c$ by looking at the asymptote in very strong inversion. For a short-channel transistor in strong inversion and saturation, the normalized $G_m/I_D$ is given by
\begin{equation}
  \frac{G_m\,n\,U_T}{I_D} = \frac{1}{\lambda_c \, IC} = \frac{I_{spec}}{\lambda_c \, I_D}.
\end{equation}
So if we plot $I_{spec}/(G_m\,n\,U_T)$ it will have a minimum at $\lambda_c$.

In [116]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))

lambdacext=np.zeros(Npts)

for k in range(0,Npts):
    lambdacext[k]=Ispec/(Gm[k]*nUT)

lambdac0=np.min(lambdacext)
Lsat0=lambdac0*Leff
Nmax=np.where(lambdacext == lambdac0)[0]
IDext=ID[Nmax[0]]

display(Latex(f'$\\lambda_c =$ {lambdac0:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat0/1e-9:.3f} $nm$'))
display(Latex(f'$I_{{D,ext}} =$ {IDext/1e-3:.3f} $mA$'))

plt.loglog(ID,lambdacext,'r-o', markersize=msize, markevery=mevery)
plt.loglog([1e-10,IDext],[lambdac0,lambdac0],'k--', linewidth=lw)
plt.loglog([IDext,IDext],[1e-1,lambdac0],'k--', linewidth=lw)
plt.loglog(ID[Nmax],lambdacext[Nmax],'ko', markersize=5)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.ylabel('$I_{spec}/(G_m\\,n\\,U_T)$ [-]')
plt.ylim(1e-1,1e5)
plt.annotate(f'$\\lambda_c =$ {lambdac0:.3f}', size=9,
             xy=(1e-10, lambdac0), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_D =$ {IDext/1e-3:.1f} mA', size=9,
             xy=(IDext, 1e-1), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac0:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
plt.text(0.7, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_short_lambdac_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

In [117]:
#The values of n, Ispecsq, Ispec are updated to the extracted values n0, Ispecsq0 and Ispec
#in order to keep always the same script for the plots that are not related to an extraction
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
lambdac=lambdac0
Lsat=Lsat0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

Next=101
IDsi=np.linspace(Ispec,1e-2,Next,endpoint=True)
IDGmUTsi=np.zeros(Next)
IDGmUTvs=np.zeros(Next)

for k in range(0,Next):
    IDGmUTsi[k]=n*sqrt(IDsi[k]/Ispec)
    IDGmUTvs[k]=n*lambdac*IDsi[k]/Ispec

plt.loglog(ID,next,'r-o', markersize=msize, markevery=mevery)
plt.loglog(IDsi,IDGmUTsi,'k--', linewidth=lw)
plt.loglog(IDsi,IDGmUTvs,'k--', linewidth=lw)
plt.loglog([1e-10,Ispec],[n,n],'k--', linewidth=lw)
plt.loglog([Ispec,Ispec],[1,n],'k--', linewidth=lw)
plt.xlabel('$I_D$ [A]')
plt.xlim(1e-10,1e-2)
plt.xticks([1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3,1e-2])
plt.ylabel('$I_D/(G_m\\,U_T)$ [-]')
plt.ylim(1,1e2)
plt.annotate(f'$n =$ {n:.2f}', size=9,
             xy=(1e-10, n), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
plt.annotate(f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$', size=9,
             xy=(Ispec, 1), xycoords='data',
             xytext=(15, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$\\lambda_c =$ {lambdac0:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
plt.text(0.03, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_short_n_Ispec_lambdac')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We can now check the normalized $G_m/I_D$ characteristic.

In [118]:
n=n0
Ispecsq=Ispecsq0
Ispec=Ispec0
lambdac=lambdac0
Lsat=Lsat0

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-9:.0f} $nA$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.2f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(10, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(25, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_short_GmID_IC_direct')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is OK at the asymptotes but not good in the moderate inversion region. Notice the bump in the lower part of strong inversion. This is most probably an artifact of the PSP model. We can try to increase $I_{spec}$ and $\lambda_c$ in order to have a better fit in moderate and strong inversion.

In [119]:
n=n0
#Ispecsq=Ispecsq0
Ispecsq=410e-9
Ispec=Ispecsq*Weff/Leff
#lambdac=lambdac0
lambdac=0.15

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.0f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.0f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.2f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(20, -50), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(50, -50), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#saveFigures(savePath, '180nm_nMOS_short_GmID_IC_direct_tuned')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

The fit is now better, offering a good trade-off between moderate and strong inversion.

#### Threshold voltage extraction

In [120]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.3f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]

ICsim=np.zeros(Npts)
VT0ext=np.zeros(Npts)

nUT=n*UT

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    VT0ext[k]=VG[k]-nUT*ln(ICsim[k])
    
plt.plot(VG,VT0ext,'r-o', markersize=msize, markevery=mevery)
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$V_{T0ext}$ [V]')
#plt.ylim(0,2)
#plt.yticks(np.arange(0,1.1,0.1))
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
plt.text(0.05, 0.95, textstr, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We see a plateau in weak inversion where we can average its value to get the threshold voltage in weak inversion.

In [121]:
VGmin=0
VGmax=0.34
VGsub=VG[(VG >= VGmin) & (VG <= VGmax)]
Nsub=len(VGsub)
Nmin=np.where(VG == VGsub[0])[0][0]
Nmax=np.where(VG == VGsub[Nsub-1])[0][0]

ICsub=np.zeros(Nsub)
VT0sub=np.zeros(Nsub)

for k in range(0,Nsub):
    ICsub[k]=ID[Nmin+k]/Ispec0
    VT0sub[k]=VGsub[k]-nUT*ln(ICsub[k])

VT0wi=np.mean(VT0sub)

display(Latex(f'$V_{{T0,wi}}  =$ {VT0wi/1e-3:.0f} mV'))

plt.plot(VGsub,VT0sub,'r-o', markersize=msize, markevery=1)
plt.plot([VGmin,VGmax],[VT0wi,VT0wi], 'k--')
plt.xlabel('$V_G$ [V]')
plt.xlim(VGmin,VGmax)
#plt.xticks(np.arange(0,11,1))
plt.ylabel('$V_{T0ext}$ [V]')
plt.ylim(0,0.5)
#plt.yticks(np.arange(0,1.1,0.1))
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$V_{{T0}} =$ {VT0wi:.3f}', size=9,
             xy=(VGmin, VT0wi), xycoords='data',
             xytext=(-30, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='right', va='center')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0wi/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
plt.text(1.05, 0.5, textstr, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We can now check the $I_D$-$V_G$ curves.

In [122]:
VT0=VT0wi

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    idsim[k]=ID[k]/Ispec

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)
    
axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.2)
axs[0].set_xticks(np.arange(-0.4,1.4,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-5,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.2)
axs[1].set_xticks(np.arange(-0.4,1.4,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We see that the threshold voltage is not correct. We can fine tune it manually.

In [123]:
#Ispecsq=1.1e-6
#Ispec=Ispecsq*W/L
VT0=0.408
lambdac=0.13

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

Npts=len(VG)
VGmin=VG[0]
VGmax=VG[Npts-1]
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    idsim[k]=ID[k]/Ispec

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)
    
axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.4,1.2)
axs[0].set_xticks(np.arange(-0.4,1.4,0.2))
axs[0].set_ylabel('$I_D/I_{spec}$')
axs[0].set_ylim(1e-5,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.4,1.2)
axs[1].set_xticks(np.arange(-0.4,1.4,0.2))
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We now have a good fit of the $I_D$-$V_G$ characteristic.

#### Summary

In [124]:
Ispecsq=457e-9
Ispec=Ispecsq*Weff/Leff
lambdac=0.16

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_short(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
#ax1.set_ylim(1e-6,1e2)
#ax1.set_yticks([1e-6,1e-5,1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat0/1e-9:.2f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e1)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
ax2.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1e3, 1/lambdac), xycoords='data',
             xytext=(25, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.2)
ax3.set_xticks(np.arange(-0.4,1.4,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
#ax3.set_ylim(0,50)
#ax3.set_yticks(np.arange(0,50,10))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(1e-3,1e3)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
ax4.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -25), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
ax4.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -37), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_short_direct_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

We finally get a reasonable fit of all characteristics.

In [125]:
#| label: tbl-short_sekv_parameters1
#| tbl-cap: Direct extraction of the sEKV parameters for the short-channel transistor with $\lambda_c>0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"direct with lambdac>0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={6: "short"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.272e+00 8.500e-07 1.733e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 6.500e-07 2.431e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 7.083e-07 2.456e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.266e+00 8.000e-07 2.456e-01   
short  1.000e-05 1.002e-05 1.300e-07 7.115e-08 1.370e+00 4.570e-07 4.080e-01   

         lambdac      Lsat                      Comment  
long   0.000e+00 0.000e+00        direct with lambdac=0  
long   0.000e+00 0.000e+00  optimization with lambdac=0  
long   5.500e-02 5.468e-07  optimization with lambdac>0  
medium 0.000e+00 0.000e+00        direct with lambdac=0  
medium 0.000e+00 0.000e+00  optimization with lambdac=0  
medium 8.000e-02 8.089e-08  optimization with lambdac>0  
short  1.600e-01 8.447e-09        direct with lambdac>0

### Extraction using optimization

#### Specific current $I_{spec}$ and $\lambda_c$ extraction

We can extract the slope factor $n$, the specific current $I_{spec}$ and the velocity saturation parameter $\lambda_c$ using curve-fitting.

In [126]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def GmIDfit4(ID,n,Ispec,lambdac):
    nUT=n*UT
    IC=ID/Ispec
    gmsid=gmsid_ic_short(IC,lambdac)
    return gmsid/nUT

Npts=len(VG)
GmIDsim=np.zeros(Npts)

for k in range(0,Npts):
    GmIDsim[k]=Gm[k]/ID[k]

nini=n0
Ispecini=Ispec0
lambdacini=0.1

pars, cov = curve_fit(f=GmIDfit4, xdata=ID, ydata=GmIDsim, p0=[nini,Ispecini,lambdacini], )
n4=pars[0]
Ispec4=pars[1]
lambdac4=pars[2]
Ispecsq4=Ispec4/(Weff/Leff)
Lsat4=lambdac4*Leff

n=n4
Ispecsq=Ispecsq4
Ispec=Ispec4
lambdac=lambdac4
Lsat=Lsat4

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$1/\\lambda_c =$ {1/lambdac:.2f}'))
display(Latex(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

ICsim=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)

for k in range(0,Npts):
    ICsim[k]=ID[k]/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

plt.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
plt.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
plt.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
plt.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
plt.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
plt.loglog(ICsim,gmidsim,'ro', markersize=msize, markevery=2)
plt.loglog(ICmod,gmidmod,'b-')
plt.xlim(1e-3,1e3)
#plt.xticks(np.arange(0,11,1))
plt.xlabel('$IC$ [-]')
plt.ylim(1e-2,)
#plt.yticks(np.arange(0,1.1,0.1))
plt.ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
#plt.legend(loc='lower right')
#plt.legend(loc='center left', fontsize=14, bbox_to_anchor=(1, 0.5))
plt.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -30), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
plt.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -40), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.1f} $\\mu A$',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.2f} nm'))
plt.text(0.03, 0.05, textstr, ha='left', va='bottom', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 1200x900 with 1 Axes>

We get a good fit across all regions.

#### Threshold voltage extraction

In [127]:
# Import curve fitting package from scipy
from scipy.optimize import curve_fit

def logIDVGfit2(VG,VT0):
    vps=(VG-VT0)/nUT
    IC=ic_vps_lambert(vps,lambdac)
    return ln(IC)

idsim=np.zeros(Npts)
logidsim=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec4
    logidsim[k]=ln(idsim[k])

nUT=n*UT
VT0ini=0.4
    
pars, cov = curve_fit(f=logIDVGfit2, xdata=VG, ydata=logidsim, p0=VT0ini)
VT04=pars[0]

VT0=VT04

display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(9, 3.5), constrained_layout=True)

VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idmod=np.zeros(Npts)

for k in range(0,Npts):
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_lambert(vps[k],lambdac)

axs[0].semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[0].semilogy(VGT,idmod, 'b-', label='sEKV')
axs[0].set_xlabel('$V_G-V_{T0}$ [V]')
axs[0].set_xlim(-0.5,)
axs[0].set_ylabel('$I_D/I_{spec}$')
#axs[0].set_ylim(1e-5,1e3)
axs[0].legend(loc='upper left')
textstr = '\n'.join((
    mosinfo,
    f'$n =$ {n:.2f}',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$V_{{T0}} =$ {VT0:.3f} V',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.2f} nm'))
axs[0].text(0.65, 0.05, textstr, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
axs[1].plot(VGT,idmod, 'b-', label='sEKV')
axs[1].set_xlabel('$V_G-V_{T0}$ [V]')
axs[1].set_xlim(-0.5,)
axs[1].set_ylabel('$I_D/I_{spec}$')
axs[1].set_ylim(0,)
axs[1].legend(loc='lower right')
axs[1].text(0.05, 0.95, textstr, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2700x1050 with 2 Axes>

We finally get a very good fit!

#### Summary

In [128]:
display(Latex(f'$n  =$ {n:.2f}'))
display(Latex(f'$I_{{spec}} =$ {Ispec/1e-6:.3f} $\\mu A$'))
display(Latex(f'$I_{{spec\\Box}} =$ {Ispecsq/1e-9:.0f} $nA$'))
display(Latex(f'$V_{{T0}}  =$ {VT0/1e-3:.0f} mV'))
display(Latex(f'$\\lambda_c =$ {lambdac:.3f}'))
display(Latex(f'$L_{{sat}} =$ {Lsat/1e-9:.3f} $nm$'))

Npts=len(VG)
logICmin=-3
logICmax=3
ICmin=pow(10,logICmin)
ICmax=pow(10,logICmax)
ICmod=np.logspace(logICmin,logICmax,Npts,endpoint=True,base=10.0)
VGT=np.zeros(Npts)
vps=np.zeros(Npts)
idsim=np.zeros(Npts)
ICsim=np.zeros(Npts)
idmod=np.zeros(Npts)
gmssim=np.zeros(Npts)
gmsmod=np.zeros(Npts)
gmidsim=np.zeros(Npts)
gmidmod=np.zeros(Npts)

for k in range(0,Npts):
    idsim[k]=ID[k]/Ispec
    ICsim[k]=idsim[k]
    gmssim[k]=Gm[k]*nUT/Ispec
    gmidsim[k]=Gm[k]*nUT/ID[k]
    VGT[k]=VG[k]-VT0
    vps[k]=VGT[k]/nUT
    idmod[k]=ic_vps_lambert(vps[k],lambdac)
    gmsmod[k]=gms_ic_short(ICmod[k],lambdac)
    gmidmod[k]=gmsid_ic_short(ICmod[k],lambdac)

fig = plt.figure(figsize=(10, 6))

ax1 = fig.add_subplot(2, 2, 1)
ax2 = fig.add_subplot(2, 2, 2)
ax3 = fig.add_subplot(2, 2, 3, sharex = ax1)
ax4 = fig.add_subplot(2, 2, 4, sharex = ax2)

ax1.semilogy(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax1.semilogy(VGT,idmod, 'b-', label='sEKV')
#ax1.set_xlabel('$V_G-V_{T0}$ [V]')
#ax1.set_xlim(-0.3,0.7)
#ax1.set_xticks(np.arange(-0.3,0.8,0.1))
ax1.set_ylabel('$I_D/I_{spec}$ (log)')
#ax1.set_ylim(1e-6,1e2)
#ax1.set_yticks([1e-6,1e-5,1e-4,1e-3,1e-2,1e-1,1e0,1e1,1e2])
ax1.legend(loc='upper left')
ax1.tick_params('x', labelbottom=False)
textstr = '\n'.join((
    f'$n =$ {n:.2f}',
    f'$I_{{specsq}} =$ {Ispecsq/1e-9:.0f} nA',
    f'$I_{{spec}} =$ {Ispec/1e-6:.2f} $\\mu A$',
    f'$V_{{T0}} =$ {VT0/1e-3:.0f} mV',
    f'$\\lambda_c =$ {lambdac:.3f}',
    f'$L_{{sat}} =$ {Lsat/1e-9:.2f} nm'))
ax1.text(0.75, 0.05, mosinfo, ha='left', va='bottom', transform=ax1.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax2.loglog([1e-3,1],[1,1],'k--', linewidth=lw)
ax2.loglog([1,1e3],[1,sqrt(1e3)],'k--', linewidth=lw)
ax2.loglog([1,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1],[1e-3,1],'k--', linewidth=lw)
ax2.loglog([1e-3,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog([1/lambdac,1/lambdac],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog([1e-3,1e3],[1/lambdac,1/lambdac],'k--', linewidth=lw)
ax2.loglog([1/lambdac**2,1/lambdac**2],[1e-3,1/lambdac],'k--', linewidth=lw)
ax2.loglog(ICsim,gmssim, 'ro', label='Data', markersize=msize, markevery=2)
ax2.loglog(ICmod,gmsmod, 'b-', label='sEKV')
#ax2.set_xlabel('$IC$ [-]')
ax2.set_xlim(ICmin,ICmax)
ax2.set_ylabel('$G_m\\,n\\,U_T/I_{spec}$ [-]')
ax2.set_ylim(1e-3,1e1)
ax2.tick_params('x', labelbottom=False)
ax2.legend(loc='lower right')
ax2.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1e3, 1/lambdac), xycoords='data',
             xytext=(25, 0), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='left', va='center')
#ax2.text(0.65, 0.05, textstr, ha='left', va='bottom', transform=ax2.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax3.plot(VGT,idsim, 'ro', label='Data', markersize=msize, markevery=mevery)
ax3.plot(VGT,idmod, 'b-', label='sEKV')
ax3.set_xlabel('$V_G-V_{T0}$ [V]')
ax3.set_xlim(-0.4,1.2)
ax3.set_xticks(np.arange(-0.4,1.4,0.2))
ax3.set_ylabel('$I_D/I_{spec}$ (lin)')
ax3.set_ylim(0,)
#ax3.set_yticks(np.arange(0,50,10))
ax3.legend(loc='lower right')
ax3.text(0.05, 0.95, textstr, ha='left', va='top', transform=ax3.transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

ax4.loglog([1e-3,1/lambdac],[1,1],'k--', linewidth=lw)
ax4.loglog([1,1e3],[1,1/sqrt(1e3)],'k--', linewidth=lw)
ax4.loglog([1,1],[1e-2,1],'k--', linewidth=lw)
ax4.loglog([1/lambdac,1e3],[1,1/(lambdac*1e3)],'k--', linewidth=lw)
ax4.loglog([1/lambdac,1/lambdac],[1e-2,1],'k--', linewidth=lw)
ax4.loglog([1/lambdac**2,1/lambdac**2],[1e-2,lambdac],'k--', linewidth=lw)
ax4.loglog(ICsim,gmidsim, 'ro', label='Data', markersize=msize, markevery=2)
ax4.loglog(ICmod,gmidmod, 'b-', label='sEKV')
ax4.set_xlabel('$IC$ [-]')
ax4.set_xlim(1e-3,1e3)
ax4.set_ylabel('$G_m\\,n\\,U_T/I_D$ [-]')
ax4.set_ylim(1e-2,)
ax4.legend(loc='lower left')
ax4.annotate(f'$1/\\lambda_c =$ {1/lambdac:.1f}', size=9,
             xy=(1/lambdac, 1e-2), xycoords='data',
             xytext=(0, -25), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
ax4.annotate(f'$1/\\lambda_c^2 =$ {1/lambdac**2:.0f}', size=9,
             xy=(1/lambdac**2, 1e-2), xycoords='data',
             xytext=(0, -37), textcoords='offset points',
             bbox=dict(boxstyle='square,pad=0', fc='w', ec='none'),
             arrowprops=dict(arrowstyle="-|>", shrinkA=0, capstyle='butt', ec='k', fc='k', joinstyle='miter'),
             ha='center', va='top')
#ax4.text(0.05, 0.05, textstr, ha='left', va='bottom', transform=ax4.transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
fig.subplots_adjust(hspace=0)
fig.subplots_adjust(wspace=0.3)
#saveFigures(savePath, '180nm_nMOS_short_opt_summary')
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 3000x1800 with 4 Axes>

We have an overall very good fit.

In [129]:
#| label: tbl-short_sekv_parameters
#| tbl-cap: Extraction of the sEKV parameters by optimization for the short-channel transistor with $\lambda_c>0$.

sekv_idvg_param_df.loc[len(sekv_idvg_param_df.index)] = [W,Weff,L,Leff,n,Ispecsq,VT0,lambdac,Lsat,"optimization with lambdac>0"]
sekv_idvg_param_df = sekv_idvg_param_df.rename(index={7: "short"})
sekv_idvg_param_df

W      Weff         L      Leff         n   Ispecsq       VT0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.100e-07 1.746e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.210e+00 8.173e-07 1.733e-01   
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06 1.272e+00 8.500e-07 1.733e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 6.500e-07 2.431e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.220e+00 7.083e-07 2.456e-01   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07 1.266e+00 8.000e-07 2.456e-01   
short  1.000e-05 1.002e-05 1.300e-07 7.115e-08 1.370e+00 4.570e-07 4.080e-01   
short  1.000e-05 1.002e-05 1.300e-07 7.115e-08 1.370e+00 3.649e-07 3.950e-01   

         lambdac      Lsat                      Comment  
long   0.000e+00 0.000e+00        direct with lambdac=0  
long   0.000e+00 0.000e+00  optimization with lambdac=0  
long   5.500e-02 5.468e-07  optimization with lambdac>0  
medium 0.000e+00 0.000e+00        direct with lambdac=0  
medium 0.000e+00 0.000e+00  optimization with lambdac=0  
medium 8.000e-02 8.089e-08  optimization with lambdac>0  
short  1.600e-01 8.447e-09        direct with lambdac>0  
short  9.955e-02 7.083e-09  optimization with lambdac>0

## Output characteristic

### Generating the data

In [130]:
simulationPath="./Simulations/" + type + "/idgdsvd/"
dataPath="./Data/" + type + "/"
fileName = "idgdsvd"
dataFile = dataPath + fileName + "_" + type + "_short.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

idx=6
n=sekv_idvg_param_df.iloc[idx]['n']
Ispecsq=sekv_idvg_param_df.iloc[idx]['Ispecsq']
VT0=sekv_idvg_param_df.iloc[idx]['VT0']

VS=0
VD=1.2

IC=1
Ispec=Ispecsq*Weff/Leff
ID=Ispec*IC
vps=vps_ic(IC)
nUT=n*UT
VG=VT0+nUT*vps

Npts=201
VDmin=0
VDmax=1.2
dVD=(VDmax-VDmin)/(Npts-1)

if newSim:
    paramstr = '\n'.join((
        f'.param W={W/1e-6:.2f}u L={L/1e-9:.2f}n VG={VG:.1f} VS={VS:.1f} VD={VD:.1f}',
        f'.csparam VDmin = {VDmin:.3f}',
        f'.csparam VDmax = {VDmax:.3f}',
        f'.csparam dVD = {dVD:.3f}'
    ))
    #print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationPath + fileName + ".log", 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

### Importing and plotting the data

#### I~D~ and G~ds~ versus V~D~

In [131]:
df_idgdsvd=pd.read_table(dataFile, sep=' +', engine='python')
VD=df_idgdsvd['v-sweep'].to_numpy()
ID=df_idgdsvd['ID'].to_numpy()
Gds=df_idgdsvd['Gds'].to_numpy()

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)
    
axs[0].plot(VD, ID/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
mosinfo = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-9:.0f} nm',
    f'$V_S =$ {VS:.0f} V',
    f'$IC \\cong$ {IC:.0f}',
    f'$V_G =$ {VG/1e-3:.0f} mV'))
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VD, abs(Gds)/1e-6, 'r-o', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

In [132]:
def diff(y, dx):
    N=len(y)
    dydx=np.zeros(N)
    dydx[0]=(y[1]-y[0])/dx
    dydx[1]=(y[2]-y[0])/(2*dx)
    for k in range(2,N-2):
        dydx[k]=(y[k-2]-8*y[k-1]+8*y[k+1]-y[k+2])/(12*dx)
    dydx[N-2]=(y[N-1]-y[N-3])/(2*dx)
    dydx[N-1]=(y[N-1]-y[N-2])/dx
    return dydx

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]
Gdsnum=np.zeros(Npts)
dVD=VD[1]-VD[0]
Gdsnum=diff(ID,dVD)

plt.semilogy(VD, Gds/1e-6,'ro', label='Data', markersize=msize, markevery=mevery)
plt.semilogy(VD, Gdsnum/1e-6,'b-', label='Num. diff.')
plt.xlabel('$V_D$ [V]')
plt.xlim(VDmin,VDmax)
#plt.xticks(np.arange(0,2.2,0.2))
plt.ylabel('$G_{ds}$ [$\\mu A/V$]')
#plt.ylim(1e-11,1e-3)
#plt.yticks([1e-11,1e-10,1e-9,1e-8,1e-7,1e-6,1e-5,1e-4,1e-3])
plt.legend(loc='lower left')
plt.text(0.75, 0.5, mosinfo, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 1200x900 with 1 Axes>

#### Filtering the outliers

In [133]:
VDmini=0.15
VDmaxi=1.2

VDsub=VD[(VD >= VDmini) & (VD <= VDmaxi)]
Nsub=len(VDsub)
Nmin=np.where(VD == VDsub[0])[0][0]
Nmax=np.where(VD == VDsub[Nsub-1])[0][0]

IDsub=np.zeros(Nsub)
Gdssub=np.zeros(Nsub)

for k in range(0,Nsub):
    IDsub[k]=ID[Nmin+k]
    Gdssub[k]=Gds[Nmin+k]

Nfil=Npts-Nsub
VDfil=np.zeros(Nfil)
IDfil=np.zeros(Nfil)
Gdsfil=np.zeros(Nfil)

for k in range(0,Nfil):
    VDfil[k]=VD[k]
    IDfil[k]=ID[k]
    Gdsfil[k]=Gds[k]

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)

axs[0].plot(VDfil, IDfil/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[0].plot(VDsub, IDsub/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,2.2,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VDfil, abs(Gdsfil)/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[1].semilogy(VDsub, abs(Gdssub)/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<Figure size 2400x900 with 2 Axes>

#### Extracting the CLM parameter

In [134]:
from scipy.stats import linregress

slope, intercept, _, _, _ = linregress(VDsub, IDsub)
Gdsext=slope
ID0ext=intercept
VEext=-ID0ext/Gdsext
lambdaext=-VEext/L

display(Latex(f'$G_{{ds}} =$ {Gdsext/1e-6:.3f} $\\mu A/V$'))
display(Latex(f'$I_{{D0}} =$ {ID0ext/1e-6:.3f} $\\mu A$'))
display(Latex(f'$V_E =$ {VEext:.3f} $V$'))
display(Latex(f'$\\lambda =$ {lambdaext/1e6:.3f} $V/\\mu m$'))

Npts=len(VD)
VDmin=VD[0]
VDmax=VD[Npts-1]

IDfit=np.zeros(Npts)
Gdsfit=np.zeros(Npts)

for k in range(0,Npts):
#    IDfit[k]=ID0ext+Gdsext*VD[k]
    IDfit[k]=Gdsext*(VD[k]-VEext)
    Gdsfit[k]=Gdsext

fig, axs = plt.subplots(ncols=2, nrows=1, figsize=(8, 3), constrained_layout=True)

axs[0].plot(VDfil, IDfil/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[0].plot(VDsub, IDsub/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[0].plot(VD, IDfit/1e-6, 'k--', label='Fit')
axs[0].set_xlabel('$V_D$ [V]')
axs[0].set_xlim(VDmin,VDmax)
#axs[0].set_xticks(np.arange(0,1.6,0.2))
axs[0].set_ylabel('$I_D$ [$\\mu A$]')
axs[0].set_ylim(0,)
#axs[0].legend(loc='upper left')
#axs[0].text(0.7, 0.05, mosinfo, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
#         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
textstr1 = '\n'.join((
    f'$I_{{D0}} =$ {ID0ext/1e-6:.1f} $\\mu A$',
    f'$G_{{ds}} =$ {Gdsext/1e-6:.1f} $\\mu A/V$',
    f'$V_E =$ {VEext:.3f} V',
    f'$\\lambda =$ {lambdaext/1e6:.3f} $V/\\mu m$'))
axs[0].text(0.6, 0.05, textstr1, ha='left', va='bottom', transform=axs[0].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})

axs[1].semilogy(VDfil, abs(Gdsfil)/1e-6, 'b-o', label='Outliers', markersize=msize, markevery=mevery)
axs[1].semilogy(VDsub, abs(Gdssub)/1e-6, 'r-o', label='Selected', markersize=msize, markevery=mevery)
axs[1].semilogy(VD, Gdsfit/1e-6, 'k--', label='Fit')
axs[1].set_xlabel('$V_D$ [V]')
axs[1].set_xlim(VDmin,VDmax)
#axs[1].set_xticks(np.arange(0,2.2,0.2))
axs[1].set_ylabel('$|G_{ds}|$ [$\\mu A/V$]')
#axs[1].set_ylim(0,)
#axs[1].legend(loc='lower right')
axs[1].text(0.7, 0.95, mosinfo, ha='left', va='top', transform=axs[1].transAxes, size=9,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.show()

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<Figure size 2400x900 with 2 Axes>

In [135]:
#| label: tbl-short_clm_parameters1
#| tbl-cap: CLM parameters extracted for the short-channel transistor in moderate inversion.

sekv_idvd_param_df.loc[len(sekv_idvd_param_df.index)] = [W,Weff,L,Leff,IC,Gdsext,ID0ext,VEext,lambdaext,"moderate"]
sekv_idvd_param_df = sekv_idvd_param_df.rename(index={2: "short"})
sekv_idvd_param_df

W      Weff         L      Leff  IC       Gds       ID0  \
long   1.000e-05 1.002e-05 1.000e-05 9.941e-06   1 2.105e-07 6.119e-07   
medium 1.000e-06 1.020e-06 1.000e-06 9.412e-07   1 5.124e-07 7.048e-07   
short  1.000e-05 1.002e-05 1.300e-07 7.115e-08   1 2.132e-05 6.341e-06   

               VE    lambda   Comment  
long   -2.907e+00 2.907e+05  moderate  
medium -1.375e+00 1.375e+06  moderate  
short  -2.974e-01 2.288e+06  moderate

## Noise

In this section we will extract the flicker noise parameters to be used with sEKV and check the white noise power spectral density (PSD) for the short channel transistor. We first will set the bias condition in terms of $IC$ and calculate the input-referred white noise to compare it to the result obtained from the PSP simulations.

### Setting bias conditions

In [136]:
#n=1.37
#VT0=410e-3
#Ispecsq=750e-9
#lambdac=0.125
tox=2.2404e-09
Cox=epsilonox*epsilon0/tox

idx=6
n=sekv_idvg_param_df.iloc[idx]['n']
Ispecsq=sekv_idvg_param_df.iloc[idx]['Ispecsq']
VT0=sekv_idvg_param_df.iloc[idx]['VT0']
lambdac=sekv_idvg_param_df.iloc[idx]['lambdac']

VDD=1.8
IC=1
Ispec=Ispecsq*Weff/Leff
ID=Ispec*IC
#qs=q_ic(IC)
vps=vps_ic(IC)
nUT=n*UT
VG=VT0+nUT*vps
VS=0
gms=gms_ic(IC)
Gmekv=Ispec/nUT*gms
gammanekv=gamman_ic(IC,n)
Rnthekv=gammanekv/Gmekv
Snthekv=4*kT*Rnthekv
Vnthekv0=sqrt(Snthekv)
Av=10
RL=Av/Gmekv
VRL=ID*RL
VDS=VDD-VRL
VDSsat=UT*vdssat_ic(IC)
region="saturation" if VDS > VDSsat else "linear"

display(Latex(f'$W =$ {W/1e-6:.0f} $\\mu m$'))
display(Latex(f'$L =$ {L/1e-9:.0f} $nm$'))
display(Latex(f'$IC =$ {IC:.1f}'))
display(Latex(f'$I_{{D}} =$ {ID/1e-6:.3f} $\\mu A$'))
display(Latex(f'$V_{{G}} =$ {VG:.3f} $V$'))
display(Latex(f'$V_{{S}} =$ {VS:.3f} $V$'))
display(Latex(f'$G_{{m}} =$ {Gmekv/1e-6:.3f} $\\mu A/V$'))
display(Latex(f'$\\gamma_n =$ {gammanekv:.3f}'))
display(Latex(f'$R_{{n,th}} =$ {Rnthekv/1e3:.3f} $k \\Omega$'))
display(Latex(f'$S_{{n,th}} =$ {Snthekv:.3e} $V^2/Hz$'))
display(Latex(f'$V_{{n,th}} =$ {Vnthekv0/1e-9:.3f} $nV/\\sqrt{{Hz}}$'))
display(Latex(f'$A_v =$ {Av:.0f}'))
display(Latex(f'$R_L =$ {RL/1e3:.3f} $k \\Omega$'))
display(Latex(f'$V_{{DD}} =$ {VDD:.3f} $V$'))
display(Latex(f'$V_{{RL}} =$ {VRL:.3f} $V$'))
display(Latex(f'$V_{{DS}} =$ {VDS:.3f} $V$'))
display(Latex(f'$V_{{DSsat}} =$ {VDSsat:.3f} $V$'))
print(f'The transistor is biased in the {region} region')

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

...

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

The transistor is biased in the saturation region


### Extract operating point information

In [137]:
simulationPath="./Simulations/" + type + "/noise/"
dataPath="./Data/" + type + "/"
fileName = "noise"
dataFile = dataPath + fileName + "_" + type + "_short.op.dat"
opFile = simulationPath + fileName + ".op.dat"
paramFile = simulationPath + fileName + ".op.par"
simulationFile = simulationPath + fileName + ".op.cir"
simulationLog = simulationPath + fileName + ".op.log"
simulationData = simulationPath + fileName + ".op.dat"

if newSim:
    paramstr = '\n'.join((
        f'.param VDD={VDD:.1f} VG={VG:.3f} RL={RL/1e3:.3f}k',
        f'.param W={W/1e-6:.0f}u L={L/1e-9:.0f}n'
    ))
    print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationLog, 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

We can extract the values of the PSP noise parameters from the operating point informations.

In [138]:
mosop_df=pd.read_table(dataFile, sep=r'\s+', dtype=np.float64, engine='python')
mosop_df=mosop_df.rename(columns={'@n.xn.nsg13_lv_nmos[weff]': 'Transistor',
                              '@n.xn.Nsg13_lv_nmos[weff]': 'Weff',
                              '@n.xn.Nsg13_lv_nmos[leff]': 'Leff',
                              '@n.xn.Nsg13_lv_nmos[ids]': 'IDS',
                              '@n.xn.Nsg13_lv_nmos[gm]': 'Gm',
                              '@n.xn.Nsg13_lv_nmos[gds]': 'Gds',
                              '@n.xn.Nsg13_lv_nmos[sid]': 'Snidth',
                              '@n.xn.Nsg13_lv_nmos[sqrtsfw]': 'Vninth',
                              '@n.xn.Nsg13_lv_nmos[sfl]': 'Snidfl @ 1Hz',
                              '@n.xn.Nsg13_lv_nmos[sqrtsff]': 'Vninfl @ 1kHz',
                              '@n.xn.Nsg13_lv_nmos[fknee]': 'fk'
                    })
mosop_df['Transistor'] = mosop_df['Transistor'].astype(str)
mosop_df.at[0, 'Transistor'] = 'Mn'
mosop_df.set_index('Transistor', inplace=True)
mosop_df.rename_axis(index=None, inplace=True)

Weffpsp=mosop_df.at['Mn','Weff']
Leffpsp=mosop_df.at['Mn','Leff']
Gmpsp=mosop_df.at['Mn','Gm']
Snidthpsp=mosop_df.at['Mn','Snidth']
Snidfl1Hzpsp=mosop_df.at['Mn','Snidfl @ 1Hz']
Snthpsp=Snidthpsp/Gmpsp**2
Vnthpsp0=mosop_df.at['Mn','Vninth']
Snfl1Hzpsp=Snidfl1Hzpsp/Gmpsp**2
Vnfl1Hzpsp=sqrt(Snfl1Hzpsp)
Vnfl1kHzpsp=mosop_df.at['Mn','Vninfl @ 1kHz']
KFpsp=Snfl1Hzpsp*Weffpsp*Leffpsp*Cox # Definition from EKV 2.6
KFshort=KFpsp
rhopsp=KFpsp/(4*kT*Cox)
rhoshort=rhopsp
AFpsp=log(Snfl1Hzpsp/Vnfl1kHzpsp**2)/3
fkpsp=mosop_df.at['Mn','fk']
Rnthpsp=Snthpsp/(4*kT)
gammanpsp=Gmpsp*Rnthpsp

display(Latex(f'$V_{{n,th}} =$ {Vnthpsp0/1e-9:.3f} $nV/\\sqrt{{Hz}}$ (PSP)'))
display(Latex(f'$f_k=$ {fkpsp/1e3:.3f} $kHz$ (PSP)'))
display(Latex(f'$KF =$ {KFpsp:.3e} $V A s$ (PSP)'))
display(Latex(f'$\\rho =$ {rhopsp:.3e} $V m^2/(A s)$ (PSP)'))
display(Latex(f'$AF =$ {AFpsp:.3f} (PSP)'))
display(Latex(f'$R_{{n,th}} =$ {Rnthpsp/1e3:.3f} $k \\Omega$ (PSP)'))
display(Latex(f'$\\gamma_n =$ {gammanpsp:.3f} (PSP)'))

pd.set_option('display.float_format', '{:.2E}'.format)
mosop_df

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Weff     Leff      IDS       Gm      Gds   Snidth   Vninth  \
Mn 1.00E-05 7.12E-08 6.04E-05 9.51E-04 3.12E-05 1.34E-23 3.85E-09   

    Snidfl @ 1Hz  Vninfl @ 1kHz       fk  
Mn      4.73E-17       2.29E-07 3.53E+06

### Simulating noise PSD

We can now simulate the PSD and check against the EKV model.

In [139]:
simulationPath="./Simulations/" + type + "/noise/"
dataPath="./Data/" + type + "/"
fileName = "noise"
dataFile = dataPath + fileName + "_" + type + "_short.dat"
paramFile = simulationPath + fileName + ".par"
simulationFile = simulationPath + fileName + ".cir"
simulationLog = simulationPath + fileName + ".log"
simulationData = simulationPath + fileName + ".dat"

fmin=1
fmax=1e10
decPts=21

if newSim:
    paramstr = '\n'.join((
        f'.param VDD={VDD:.1f} VG={VG:.3f} RL={RL/1e3:.3f}k',
        f'.param W={W/1e-6:.0f}u L={L/1e-9:.0f}n',
        f'.csparam fmin = {fmin:.0e}',
        f'.csparam fmax = {fmax:.0e}',
        f'.csparam decPts = {decPts:.0f}'
    ))
    print(paramstr)
    with open(paramFile, 'w') as f:
        f.write(paramstr)
    print('Starting ngspice simulation...\n')
    result = subprocess.run(f"""ngspice_con -b -o "{simulationLog}" "{simulationFile}" """, shell=True, capture_output=True, text=True)
    if result.stderr == '':
        print("Simulation executed successfully.\n")
    else:
        print("Simulation failed with return code", result.stderr)
    print(result.stdout)
    f = open(simulationLog, 'r')
    log_contents = f.read()
    print("Contents of the log file:")
    print("‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾‾\n")
    print (log_contents)
    # We copy the simulation results to the dat folder
    shutil.copy2(simulationData, dataFile)

In [140]:
df_noise=pd.read_table(dataFile, sep=' +', engine='python')
freq=df_noise['frequency'].to_numpy()
Vninpsp=df_noise['inoise_spectrum'].to_numpy()
Vnoutpsp=df_noise['onoise_spectrum'].to_numpy()

Type='nMOS (t-t)'

Npts=len(freq)
fmin=freq[0]
fmax=freq[Npts-1]

Vnthekv=np.zeros(Npts)
Snflekv=np.zeros(Npts)
Vnflekv=np.zeros(Npts)

for k in range(0,Npts):
    Vnthekv[k]=Vnthekv0
    Snflekv[k]=KFpsp/(Weff*Leff*Cox*freq[k])
    Vnflekv[k]=sqrt(Snflekv[k])

plt.loglog(freq, Vnoutpsp,'r-', label='Output noise (PSP)')
plt.loglog(freq, Vninpsp,'b-', label='Input noise (PSP)')
plt.loglog(freq, Vnthekv,'k--', label='White input noise (sEKV)')
plt.loglog(freq, Vnflekv,'k-.', label='Flicker input noise (model)')
#plt.loglog([fk,fk],[1e-10,Vnth],'k--')
plt.xlim(fmin,fmax)
#plt.xticks([1e0,1e1,1e2,1e3,1e4,1e5,1e6,1e7,1e8,1e9])
plt.xlabel('Frequency [Hz]')
plt.ylim(1e-9,1e-5)
plt.ylabel('$\\sqrt{S_{nout}}$ and $\\sqrt{S_{nin}}$ $[V/\\sqrt{Hz}]$')
plt.legend(loc='lower left', fontsize=9)
#plt.legend(loc='center left', fontsize=9, bbox_to_anchor=(1, 0.5))
textstr1 = '\n'.join((
    Type,
    f'$W =$ {W/1e-6:.0f} $\\mu m$',
    f'$L =$ {L/1e-9:.0f} $nm$'))
textstr2 = '\n'.join((
    f'$IC =$ {IC:.0f}',
    f'$V_G =$ {VG:.3f} V',
    f'$V_{{DS}} =$ {VDS:.3f} V',
    f'$R_L =$ {RL/1e3:.1f} $k\\Omega$'))
textstr3 = '\n'.join((
    f'$G_m =$ {Gmpsp/1e-6:.3f} $\\mu A/V$ (PSP)',
    f'$G_m =$ {Gmekv/1e-6:.3f} $\\mu A/V$ (EKV)',
    f'$\\sqrt{{S_{{in,th}}}} =$ {Vnthpsp0:.3e} (PSP)',
    f'$\\sqrt{{S_{{in,th}}}} =$ {Vnthekv0:.3e} (EKV)',
#    f'$R_{{n,th}} =$ {Rnthpsp/1e3:.3f} $k\\Omega$ (PSP)',
#    f'$R_{{n,th}} =$ {Rnthekv/1e3:.3f} $k\\Omega$ (EKV)',
    f'$\\gamma_n =$ {gammanpsp:.3f} (PSP)',
    f'$\\gamma_n =$ {gammanekv:.3f} (EKV)',
    f'$KF =$ {KFpsp:.3e} $V A s$ (PSP)',
    f'$\\rho =$ {rhopsp:.3e} $V m^2/(A s)$ (PSP)',
    f'$AF =$ {AFpsp:.3f} (PSP)',
    f'$f_k =$ {fkpsp/1e3:.3f} kHz (PSP)'))
plt.text(0.4, 0.95, textstr1, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.text(0.7, 0.95, textstr2, ha='left', va='top', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
plt.text(1.05, 0.5, textstr3, ha='left', va='center', size=9, transform=plt.gca().transAxes,
         bbox={'facecolor':'w', 'alpha':1.0, 'pad':5})
#plt.text(fk, 1e-9, '$f_k =$'+f'{fk/1e3:.0f} kHz', ha='left', va='bottom', size=14)
#plt.text(1e2, Vnth, '$\sqrt{S_{nin,th}} =$'+f'{Vnth/1e-9:.1f} '+'$nV/\sqrt{Hz}$', ha='center', va='bottom', size=14)
#saveFigures(savePath, 'Input_referred_noise_PSD')
plt.show()

'created' timestamp seems very low; regarding as unix timestamp


'modified' timestamp seems very low; regarding as unix timestamp


<Figure size 1200x900 with 1 Axes>

The flicker noise parameter for the long- and short-channel transistors are different as shown below

In [141]:
#| label: tbl-short_noise_parameters
#| tbl-cap: Extraction of the noise parameters for the short-channel transistor.

KFn=KFpsp
rhon=rhopsp
AFn=AFpsp

sekv_noise_param_df.loc[len(sekv_noise_param_df.index)] = [W,Weff,L,Leff,IC,KFn,AFn,rhon,"moderate"]
sekv_noise_param_df = sekv_noise_param_df.rename(index={2: "short"})
sekv_noise_param_df

W     Weff        L     Leff  IC       KF       AF      rho  \
long   1.00E-05 1.00E-05 1.00E-05 9.94E-06   1 3.18E-24 1.00E+00 1.24E-02   
medium 1.00E-06 1.02E-06 1.00E-06 9.41E-07   1 2.21E-24 1.00E+00 8.64E-03   
short  1.00E-05 1.00E-05 1.30E-07 7.12E-08   1 5.76E-25 1.00E+00 2.25E-03   

         Comment  
long    moderate  
medium  moderate  
short   moderate

We will keep the long-channel value since it is larger.

# Extrinsic capacitances

## Junction capacitances

The calculation of the junction capacitances depends on the value used for the **SWJUNCAP** parameter. In this PDK **SWJUNCAP** is equal to 3 for which the junction area $AB$, junction length of side-wall capacitance along the STI edge $LS$ and junction length of the side-wall capacitance along the gate edge $LG$ are calculated according to

\begin{align}
  AB &= AS,\\
  LS &= PS-W_E,\\
  LG &= W_E,\\
\end{align}

where $AS$ is the source junction area and $PS$ the total source junction perimeter and

\begin{align}
  AB &= AD,\\
  LS &= PD-W_E,\\
  LG &= W_E,\\
\end{align}

where $AD$ is the drain junction area and $PD$ the total drain junction perimeter.

The total junction capacitance on the source $CJS$ and drain side $CJD$ are then given by

\begin{align}
  CJS &= AS \cdot CJORBOT + (PS-W_E) \cdot CJORSTI + W_E \cdot CJORGAT,\\
  CJD &= AD \cdot CJORBOT + (PD-W_E) \cdot CJORSTI + W_E \cdot CJORGAT,
\end{align}

where:

  * **CJORBOT** is the zero-bias bottom capacitance per unit-area,
  * **CJORSTI** is the zero-bias capacitance per unit-of-length along the STI-edge,
  * **CJORGAT** is the zero-bias capacitance per unit-of-length along the gate-edge.

The above junction capacitance parameters are extracted directly from the PDK. We will use the the zero-bias bias value of th various junctions capacitances.

If $AS$, $PD$, $AD$ and $PD$ are not specified, they are calculated automatically in the sg13g2_moslv_mod.lib file.

In the circuit examples, we will calculate $AS$, $PD$, $AD$ and $PD$ for avoiding the automatic cal.culation

In [142]:
# Values taken from the cornerMOSlv.lib file for t-t
sg13g2_lv_nmos_cjorbot= 1.0000
sg13g2_lv_nmos_cjorsti= 1.0000
sg13g2_lv_nmos_cjorgat= 1.0000

# Values taken from the sg13g2_moslv_parm.lib file for t-t
cjorbot = 0.00097636*sg13g2_lv_nmos_cjorbot 
cjorsti = 2.5279e-11*sg13g2_lv_nmos_cjorsti
cjorgat = 3e-11*sg13g2_lv_nmos_cjorgat

# sEKV parameters
CJn = cjorbot
CJSWSTIn = cjorsti
CJSWGATn = cjorgat

display(Latex(f'$CJn =$ {CJn:.3e} $\\frac{{F}}{{m^2}}$'))
display(Latex(f'$CJSWSTIn =$ {CJSWSTIn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$CJSWGATn =$ {CJSWGATn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$CJn =$ {CJn*1e3:.3f} $\\frac{{fF}}{{\\mu m^2}}$'))
display(Latex(f'$CJSWSTIn =$ {CJSWSTIn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))
display(Latex(f'$CJSWGATn =$ {CJSWGATn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

In [143]:
#| label: tbl-junction_parameters
#| tbl-cap: Extraction of the junction capacitance parameters.

sekv_juncap_param_df={
    "Zero-bias junction capacitance": [CJn, CJSWSTIn, CJSWGATn],
    "Comment": "extracted from PDK"
}
index_labels=["Bottom cap per area","Side-wall cap per unit length (along STI)","Side-wall cap per unit length (along gate)"]
sekv_juncap_param_df=pd.DataFrame(sekv_juncap_param_df, index=index_labels)
sekv_juncap_param_df

Zero-bias junction capacitance  \
Bottom cap per area                                               9.76E-04   
Side-wall cap per unit length (along STI)                         2.53E-11   
Side-wall cap per unit length (along gate)                        3.00E-11   

                                                       Comment  
Bottom cap per area                         extracted from PDK  
Side-wall cap per unit length (along STI)   extracted from PDK  
Side-wall cap per unit length (along gate)  extracted from PDK

## Overlap capacitances

In PSP, the gate-to-source and gate-to-drain overlap capacitances are equal and given by

\begin{equation}
  CGOV = \epsilon_{ox} \cdot \frac{W_{E,CV} \cdot LOV}{TOXOV},
\end{equation}

where $W_{E,CV}$ has already been defined above and is repeated here

The effective length and width for the calculation of the intrinsic and overlap acacitances are defined as

\begin{align}
  L_{E,CV} &= L + \Delta L_{CV},\\
  W_{E,CV} &= W + \Delta W_{CV},
\end{align}

where

\begin{align}
  \Delta L_{CV} &= 2\,LAP - \Delta L_{PS} - DLQ,\\
  \Delta W_{CV} &= 2\,WOT - \Delta W_{OD} - DWQ.
\end{align}

As mentioned above, for the IHP 130nm for nMOS $\Delta L_{PS}=0$ and $\Delta W_{OD}=0$ so that

\begin{align}
  \Delta L_{CV} &= 2\,LAP - DLQ,\\
  \Delta W_{CV} &= 2\,WOT- DWQ.
\end{align}



In [144]:
# Values taken from the cornerMOSlv.lib file for t-t
sg13g2_lv_nmos_toxovo = 1.0000

# Values taken from the sg13g2_moslv_parm.lib file for t-t
pre_layout = 1.0
epsroxo = 3.9
# CGSo overlap capacitance per unit width
toxovo = 2.2404e-09*sg13g2_lv_nmos_toxovo
lov = 2.9423e-08-((1-pre_layout)*9e-09)
CGSOn = epsilon0*epsroxo*lov/toxovo

# CGDo overlap capacitance per unit width
# toxovdo = 2e-09
# CGDOn = epsilon0*epsroxo*lov/toxovdo
CGDOn = CGSOn

# CGBo overlap capacitance per unit length
cgbovl = 4.4409e-28
CGBOn = cgbovl/LEN

print("Gate-to-source and gate-to-drain overlap capacitances per effective unit width")
display(Latex(f'$C_{{GSo}} =$ {CGSOn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GDo}} =$ {CGDOn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GSo}} =$ {CGSOn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))
display(Latex(f'$C_{{GDo}} =$ {CGDOn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))

print("\nGate-to-bulk overlap capacitances per effective unit length")
display(Latex(f'$C_{{GBo}} =$ {CGBOn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GBo}} =$ {CGBOn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))

Gate-to-source and gate-to-drain overlap capacitances per effective unit width


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>


Gate-to-bulk overlap capacitances per effective unit length


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

In PSP, the fringing field capacitance is given by

\begin{equation}
  CFR = CFRW \cdot \frac{W_{G,CV}}{W_{EN}},
\end{equation}

where

\begin{equation}
  W_{G,CV} = W_f + \Delta W_{OD} + DWQ
\end{equation}

Since $\Delta W_{OD} = 0$ it reduces to

\begin{equation}
  W_{G,CV} = W_f + DWQ
\end{equation}

In [145]:
# Fringing field capacitance per unit width
cfrw=2e-16
CGSFn=cfrw/WEN
CGDFn=CGSFn

# Total extrinsic capacitance per unit width
CGSEn=CGSOn+CGSFn
CGDEn=CGDOn+CGDFn

print("Gate-to-source and gate-to-drain fringing capacitances per effective unit width")
display(Latex(f'$C_{{GSf}} =$ {CGSFn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GDf}} =$ {CGDFn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GSf}} =$ {CGSFn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))
display(Latex(f'$C_{{GDf}} =$ {CGDFn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))

print("Total gate-to-source and gate-to-drain extrinsic capacitances per effective unit width")
display(Latex(f'$C_{{GSe}} =$ {CGSEn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GDe}} =$ {CGDEn:.3e} $\\frac{{F}}{{m}}$'))
display(Latex(f'$C_{{GSe}} =$ {CGSEn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))
display(Latex(f'$C_{{GDe}} =$ {CGDEn*1e9:.3f} $\\frac{{fF}}{{\\mu m}}$'))

Gate-to-source and gate-to-drain fringing capacitances per effective unit width


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

Total gate-to-source and gate-to-drain extrinsic capacitances per effective unit width


<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

<IPython.core.display.Latex object>

In [146]:
#| label: tbl-overlap_parameters
#| tbl-cap: Extraction of the junction capacitance parameters.

sekv_extcap_param_df={
    "CGS per effective unit width": [CGSOn, CGSFn, CGSEn],
    "CGD per effective unit width": [CGDOn, CGDFn, CGDEn],
    "CGB per effective unit length": [CGBOn, "-", "-"],
    "Comment": "extracted from PDK"
}
index_labels=["Overlap","Fringing","Total"]
sekv_extcap_param_df=pd.DataFrame(sekv_extcap_param_df, index=index_labels)
sekv_extcap_param_df

CGS per effective unit width  CGD per effective unit width  \
Overlap                       4.53E-10                      4.53E-10   
Fringing                      2.00E-10                      2.00E-10   
Total                         6.53E-10                      6.53E-10   

         CGB per effective unit length             Comment  
Overlap                       4.44E-22  extracted from PDK  
Fringing                             -  extracted from PDK  
Total                                -  extracted from PDK

In [147]:
with pd.ExcelWriter("sEKV_ihp130nm_nmos.xlsx") as writer:
    sekv_geom_param_df.to_excel(writer, sheet_name="geometric parameters (nMOS)")
    sekv_idvg_param_df.to_excel(writer, sheet_name="idvg parameters (nMOS)")
    sekv_idvd_param_df.to_excel(writer, sheet_name="idvd parameters (nMOS)")
    sekv_noise_param_df.to_excel(writer, sheet_name="noise parameters (nMOS)")
    sekv_juncap_param_df.to_excel(writer, sheet_name="Junction cap (nMOS)")
    sekv_extcap_param_df.to_excel(writer, sheet_name="Extrinsic cap parameters (nMOS)")

# Conclusion

The sEKV parameters have been extracted for a long, medium and short nMOS transistors using the data generated from the the PDK with the PSP compact model. The overall extraction results are good.

For the long-channel transistor both the direct extraction and optimization with $\lambda_c=0$ give similar results. The fit is good up to about $IC=100$. Above that the model cannot catch the effect due to the mobility reduction due to the vertical field. Notice the very low threshold voltage which is consistent with the IHP 130nm documentation. Also, the output conductance for the long and medium length device is very high compared to what we get for the pMOS transistors. This is confirmed by the measurements, but the physical origin of this high output conductance remains unclear.

For the short-channel transistor, again the direct extraction and the optimization with $\lambda_c > 0$ give similar results. The fit is good over the whole range of $IC$. Notice the bump observed in moderate inversion coming from the PSP simulations. This bumps is probably not realistic.

Overall, the sEKV can do a good job for the long, medium and short nMOS transistors.